In [169]:
import numpy as np
import pandas as pd
import math
pd.set_option('display.max_columns', 500)
pd.options.display.float_format = '{:.2f}'.format

## Summary

This notebook imports estimates of houseolds by income level and city/county under two scenarios, "business as usual" and "meeting regional housing needs." It then calculates the greenhouse gas emissions by household from three sources: vehicle miles traveled in personal cars, household electricity usage, and household gas usage. These estimates are aggregated by city, county, and region to compare the climate impacts of the two scenarios.

## Outline
### Part A. Calculating GHGs from VMT
1. Import VMT table and norm for geographies
2. Import BAS and multiply hh counts by VMT per household by income group, then convert to GHG emissions
3. Import needs table and repeat same calcs
4. Multiply hh counts in each table by VMT per household by income group and convert to GHG emissions using emissions factor from GreenTRIP Connect
5. Aggregate at the city/county level 

### Part B. Calculating GHGs from Household Electricity Usage
1. Organize Counties by Climate Zone
2. Organize Cities by Climate Zone
3. Incorporate Electricity Usage by Zone and Emissions Factors
4. Calculate Electric Emissions from BAS Scenario
5. Calculate Electric Emissions from Needs Scenario

### Part C. Calculating GHGs from Household Gas Usage
1. Calculate Gas Usage for BAS Scenario
2. Calculate Gas Usage for Needs Scenario

### Part D. Create Table with all GHG emissions

## Part A1. Import VMT table and norm for geographies

In [170]:
#import BAS table
vmt_df=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/PUMS/Analysis Across Years/vmt_multipliers.csv", delimiter=",")
vmt_df

Place        County  All_VMT  VLI_VMT  LI_VMT  \
0              Alameda city, CA       Alameda    12378     7288    9235   
1               Albany city, CA       Alameda    11759     6669    8616   
2      American Canyon city, CA          Napa    14370     9274   11244   
3              Antioch city, CA  Contra Costa    15114     9939   11834   
4             Atherton town, CA     San Mateo    12781     8916   10928   
5              Atwater city, CA        Merced    12777     7645    9269   
6               Auburn city, CA        Placer    13600     8584   10212   
7              Belmont city, CA     San Mateo    12617     8753   10764   
8            Belvedere city, CA         Marin    11255     6954    8414   
9              Benicia city, CA        Solano    12384     7485    9040   
10            Berkeley city, CA       Alameda    11500     6410    8357   
11           Brentwood city, CA  Contra Costa    15120     9945   11840   
12            Brisbane city, CA     San Mateo    12113     8248   10260   
13          Burlingame city, CA     San Mateo    11844     7979    9991   
14           Calistoga city, CA          Napa    13279     8183   10153   
15            Campbell city, CA   Santa Clara    13559     9141   11483   
16            Capitola city, CA    Santa Cruz    12637     7163    9303   
17   Carmel-by-the-Sea city, CA      Monterey    13621     8473   10222   
18               Ceres city, CA    Stanislaus    10167     5097    6813   
19      Citrus Heights city, CA    Sacramento    13194     7932    9734   
20             Clayton city, CA  Contra Costa    14279     9105   10999   
21          Cloverdale city, CA        Sonoma    14912     9693   11536   
22              Clovis city, CA        Fresno    13144     7691    9496   
23            Coalinga city, CA        Fresno    15788    10334   12140   
24              Colfax city, CA        Placer    14017     8998   10626   
25               Colma town, CA     San Mateo    11908     8044   10056   
26             Concord city, CA  Contra Costa    12708     7533    9428   
27        Corte Madera town, CA         Marin    12178     7877    9336   
28              Cotati city, CA        Sonoma    12440     7221    9048   
29           Cupertino city, CA   Santa Clara    13433     9015   11357   
..                          ...           ...      ...      ...     ...   
168    Unincorporated_El Dorado     El Dorado    17875    14036   15936   
169       Unincorporated_Fresno        Fresno    19825    15557   17481   
170        Unincorporated_Marin         Marin    10587     7878    9207   
171    Unincorporated_Mendocino     Mendocino    14855    10363   11555   
172       Unincorporated_Merced        Merced    21507    16628   18416   
173     Unincorporated_Monterey      Monterey    15937    12015   14039   
174         Unincorporated_Napa          Napa    17554    13628   16094   
175       Unincorporated_Placer        Placer    13519     9600   11487   
176   Unincorporated_Sacramento    Sacramento    15185    11077   13083   
177  Unincorporated_San Joaquin   San Joaquin    17701    13506   15407   
178    Unincorporated_San Mateo     San Mateo    13968    11635   13837   
179  Unincorporated_Santa Clara   Santa Clara    18874    14971   17418   
180   Unincorporated_Santa Cruz    Santa Cruz    16616    13063   15178   
181       Unincorporated_Solano        Solano    16493    13123   14899   
182       Unincorporated_Sonoma        Sonoma    17414    13822   15902   
183   Unincorporated_Stanislaus    Stanislaus    14442     9325   11145   
184         Unincorporated_Yolo          Yolo    17156    13186   15494   
185         Union City city, CA       Alameda    13033     9589   11618   
186          Vacaville city, CA        Solano    13772    10402   12178   
187            Vallejo city, CA        Solano    11847     8476   10252   
188       Walnut Creek city, CA  Contra Costa    12308     8823   10942   
189          Waterford city, CA    Stanislaus    14

In [171]:
#adjust vmt factors to account for diff between "all_VMT" and "Average"
vmt_df["Adjust"]=vmt_df.Average/vmt_df.All_VMT
vmt_df["VLI_VMT_adj"]=vmt_df.VLI_VMT*vmt_df.Adjust
vmt_df["LI_VMT_adj"]=vmt_df.LI_VMT*vmt_df.Adjust
vmt_df["MoI_VMT_adj"]=vmt_df.MoI_VMT*vmt_df.Adjust
vmt_df["HI_VMT_adj"]=vmt_df.Average
vmt_df

Place        County  All_VMT  VLI_VMT  LI_VMT  \
0              Alameda city, CA       Alameda    12378     7288    9235   
1               Albany city, CA       Alameda    11759     6669    8616   
2      American Canyon city, CA          Napa    14370     9274   11244   
3              Antioch city, CA  Contra Costa    15114     9939   11834   
4             Atherton town, CA     San Mateo    12781     8916   10928   
5              Atwater city, CA        Merced    12777     7645    9269   
6               Auburn city, CA        Placer    13600     8584   10212   
7              Belmont city, CA     San Mateo    12617     8753   10764   
8            Belvedere city, CA         Marin    11255     6954    8414   
9              Benicia city, CA        Solano    12384     7485    9040   
10            Berkeley city, CA       Alameda    11500     6410    8357   
11           Brentwood city, CA  Contra Costa    15120     9945   11840   
12            Brisbane city, CA     San Mateo    12113     8248   10260   
13          Burlingame city, CA     San Mateo    11844     7979    9991   
14           Calistoga city, CA          Napa    13279     8183   10153   
15            Campbell city, CA   Santa Clara    13559     9141   11483   
16            Capitola city, CA    Santa Cruz    12637     7163    9303   
17   Carmel-by-the-Sea city, CA      Monterey    13621     8473   10222   
18               Ceres city, CA    Stanislaus    10167     5097    6813   
19      Citrus Heights city, CA    Sacramento    13194     7932    9734   
20             Clayton city, CA  Contra Costa    14279     9105   10999   
21          Cloverdale city, CA        Sonoma    14912     9693   11536   
22              Clovis city, CA        Fresno    13144     7691    9496   
23            Coalinga city, CA        Fresno    15788    10334   12140   
24              Colfax city, CA        Placer    14017     8998   10626   
25               Colma town, CA     San Mateo    11908     8044   10056   
26             Concord city, CA  Contra Costa    12708     7533    9428   
27        Corte Madera town, CA         Marin    12178     7877    9336   
28              Cotati city, CA        Sonoma    12440     7221    9048   
29           Cupertino city, CA   Santa Clara    13433     9015   11357   
..                          ...           ...      ...      ...     ...   
168    Unincorporated_El Dorado     El Dorado    17875    14036   15936   
169       Unincorporated_Fresno        Fresno    19825    15557   17481   
170        Unincorporated_Marin         Marin    10587     7878    9207   
171    Unincorporated_Mendocino     Mendocino    14855    10363   11555   
172       Unincorporated_Merced        Merced    21507    16628   18416   
173     Unincorporated_Monterey      Monterey    15937    12015   14039   
174         Unincorporated_Napa          Napa    17554    13628   16094   
175       Unincorporated_Placer        Placer    13519     9600   11487   
176   Unincorporated_Sacramento    Sacramento    15185    11077   13083   
177  Unincorporated_San Joaquin   San Joaquin    17701    13506   15407   
178    Unincorporated_San Mateo     San Mateo    13968    11635   13837   
179  Unincorporated_Santa Clara   Santa Clara    18874    14971   17418   
180   Unincorporated_Santa Cruz    Santa Cruz    16616    13063   15178   
181       Unincorporated_Solano        Solano    16493    13123   14899   
182       Unincorporated_Sonoma        Sonoma    17414    13822   15902   
183   Unincorporated_Stanislaus    Stanislaus    14442     9325   11145   
184         Unincorporated_Yolo          Yolo    17156    13186   15494   
185         Union City city, CA       Alameda    13033     9589   11618   
186          Vacaville city, CA        Solano    13772    10402   12178   
187            Vallejo city, CA        Solano    11847     8476   10252   
188       Walnut Creek city, CA  Contra Costa    12308     8823   10942   
189          Waterford city, CA    Stanislaus    14

## Part A2. Import BAS and multiply hh counts by VMT per household by income group, then convert to GHG emissions

In [172]:
# Import BAS table
bas_df=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/PUMS/Analysis Across Years/hh_by_city_and_county.csv", delimiter=",")
bas_df.drop('Unnamed: 0', axis=1, inplace=True)
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [173]:
bas_df = bas_df.merge(vmt_df, how='left', left_on = "Place",right_on = "Place")
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [174]:
#multiply each years hh counts by income by the VMT factors
bas_df["15_VLI_VMT"]=bas_df["15_VLI_hh_count"]*bas_df.VLI_VMT_adj
bas_df["15_LI_VMT"]=bas_df["15_LI_hh_count"]*bas_df.LI_VMT_adj
bas_df["15_MoI_VMT"]=bas_df["15_MoI_hh_count"]*bas_df.MoI_VMT_adj
bas_df["15_HI_VMT"]=bas_df["15_HI_hh_count"]*bas_df.HI_VMT_adj

bas_df["16_VLI_VMT"]=bas_df["16_VLI_hh_count"]*bas_df.VLI_VMT_adj
bas_df["16_LI_VMT"]=bas_df["16_LI_hh_count"]*bas_df.LI_VMT_adj
bas_df["16_MoI_VMT"]=bas_df["16_MoI_hh_count"]*bas_df.MoI_VMT_adj
bas_df["16_HI_VMT"]=bas_df["16_HI_hh_count"]*bas_df.HI_VMT_adj

bas_df["17_VLI_VMT"]=bas_df["17_VLI_hh_count"]*bas_df.VLI_VMT_adj
bas_df["17_LI_VMT"]=bas_df["17_LI_hh_count"]*bas_df.LI_VMT_adj
bas_df["17_MoI_VMT"]=bas_df["17_MoI_hh_count"]*bas_df.MoI_VMT_adj
bas_df["17_HI_VMT"]=bas_df["17_HI_hh_count"]*bas_df.HI_VMT_adj

bas_df["18_VLI_VMT"]=bas_df["18_VLI_hh_count"]*bas_df.VLI_VMT_adj
bas_df["18_LI_VMT"]=bas_df["18_LI_hh_count"]*bas_df.LI_VMT_adj
bas_df["18_MoI_VMT"]=bas_df["18_MoI_hh_count"]*bas_df.MoI_VMT_adj
bas_df["18_HI_VMT"]=bas_df["18_HI_hh_count"]*bas_df.HI_VMT_adj
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [175]:
# sum VMT by year by geography
bas_df["15_total_VMT"]=bas_df["15_VLI_VMT"]+bas_df["15_LI_VMT"]+bas_df["15_MoI_VMT"]+bas_df["15_HI_VMT"]
bas_df["16_total_VMT"]=bas_df["16_VLI_VMT"]+bas_df["16_LI_VMT"]+bas_df["16_MoI_VMT"]+bas_df["16_HI_VMT"]
bas_df["17_total_VMT"]=bas_df["17_VLI_VMT"]+bas_df["17_LI_VMT"]+bas_df["17_MoI_VMT"]+bas_df["17_HI_VMT"]
bas_df["18_total_VMT"]=bas_df["18_VLI_VMT"]+bas_df["18_LI_VMT"]+bas_df["18_MoI_VMT"]+bas_df["18_HI_VMT"]
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [176]:
#calculate ghgs from vmt
bas_df["15_vmt_ghg"]=bas_df["15_total_VMT"]*0.00052179632653806
bas_df["16_vmt_ghg"]=bas_df["16_total_VMT"]*0.00052179632653806
bas_df["17_vmt_ghg"]=bas_df["17_total_VMT"]*0.00052179632653806
bas_df["18_vmt_ghg"]=bas_df["18_total_VMT"]*0.00052179632653806
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [177]:
bas_df["15_reg_vmt"]=bas_df["15_total_VMT"].sum()
bas_df["16_reg_vmt"]=bas_df["16_total_VMT"].sum()
bas_df["17_reg_vmt"]=bas_df["17_total_VMT"].sum()
bas_df["18_reg_vmt"]=bas_df["18_total_VMT"].sum()
bas_df

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

## Part A3. Import needs table and repeat same calcs

In [178]:
# Import needs table
needs_df=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/PUMS/Analysis Across Years/needs_hh_by_city_and_county.csv", delimiter=",")
needs_df.drop('Unnamed: 0', axis=1, inplace=True)
needs_df

Place        County  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [179]:
needs_df = needs_df.merge(vmt_df, how='left', left_on = "Place",right_on = "Place")
needs_df

Place      County_x  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [180]:
#multiply each years hh counts by income by the VMT factors
needs_df["15_VLI_VMT"]=needs_df["15_VLI_hh_mod"]*needs_df.VLI_VMT_adj
needs_df["15_LI_VMT"]=needs_df["15_LI_hh_mod"]*needs_df.LI_VMT_adj
needs_df["15_MoI_VMT"]=needs_df["15_MoI_hh_mod"]*needs_df.MoI_VMT_adj
needs_df["15_HI_VMT"]=needs_df["15_HI_hh_mod"]*needs_df.HI_VMT_adj

needs_df["16_VLI_VMT"]=needs_df["16_VLI_hh_mod"]*needs_df.VLI_VMT_adj
needs_df["16_LI_VMT"]=needs_df["16_LI_hh_mod"]*needs_df.LI_VMT_adj
needs_df["16_MoI_VMT"]=needs_df["16_MoI_hh_mod"]*needs_df.MoI_VMT_adj
needs_df["16_HI_VMT"]=needs_df["16_HI_hh_mod"]*needs_df.HI_VMT_adj

needs_df["17_VLI_VMT"]=needs_df["17_VLI_hh_mod"]*needs_df.VLI_VMT_adj
needs_df["17_LI_VMT"]=needs_df["17_LI_hh_mod"]*needs_df.LI_VMT_adj
needs_df["17_MoI_VMT"]=needs_df["17_MoI_hh_mod"]*needs_df.MoI_VMT_adj
needs_df["17_HI_VMT"]=needs_df["17_HI_hh_mod"]*needs_df.HI_VMT_adj

needs_df["18_VLI_VMT"]=needs_df["18_VLI_hh_mod"]*needs_df.VLI_VMT_adj
needs_df["18_LI_VMT"]=needs_df["18_LI_hh_mod"]*needs_df.LI_VMT_adj
needs_df["18_MoI_VMT"]=needs_df["18_MoI_hh_mod"]*needs_df.MoI_VMT_adj
needs_df["18_HI_VMT"]=needs_df["18_HI_hh_mod"]*needs_df.HI_VMT_adj
needs_df

Place      County_x  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [181]:
# sum VMT by year by geography
needs_df["15_total_VMT"]=needs_df["15_VLI_VMT"]+needs_df["15_LI_VMT"]+needs_df["15_MoI_VMT"]+needs_df["15_HI_VMT"]
needs_df["16_total_VMT"]=needs_df["16_VLI_VMT"]+needs_df["16_LI_VMT"]+needs_df["16_MoI_VMT"]+needs_df["16_HI_VMT"]
needs_df["17_total_VMT"]=needs_df["17_VLI_VMT"]+needs_df["17_LI_VMT"]+needs_df["17_MoI_VMT"]+needs_df["17_HI_VMT"]
needs_df["18_total_VMT"]=needs_df["18_VLI_VMT"]+needs_df["18_LI_VMT"]+needs_df["18_MoI_VMT"]+needs_df["18_HI_VMT"]
needs_df

Place      County_x  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [182]:
#calculate ghgs from vmt
needs_df["15_vmt_ghg"]=needs_df["15_total_VMT"]*0.00052179632653806
needs_df["16_vmt_ghg"]=needs_df["16_total_VMT"]*0.00052179632653806
needs_df["17_vmt_ghg"]=needs_df["17_total_VMT"]*0.00052179632653806
needs_df["18_vmt_ghg"]=needs_df["18_total_VMT"]*0.00052179632653806
needs_df

Place      County_x  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

In [183]:
needs_df["15_reg_vmt"]=needs_df["15_total_VMT"].sum()
needs_df["16_reg_vmt"]=needs_df["16_total_VMT"].sum()
needs_df["17_reg_vmt"]=needs_df["17_total_VMT"].sum()
needs_df["18_reg_vmt"]=needs_df["18_total_VMT"].sum()
needs_df

Place      County_x  15_VLI_hh_mod  16_VLI_hh_mod  \
0              Alameda city, CA       Alameda        8260.24        8315.74   
1               Albany city, CA       Alameda        2170.94        2180.94   
2      American Canyon city, CA          Napa        1465.40        1479.90   
3              Antioch city, CA  Contra Costa       11700.43       11744.05   
4             Atherton town, CA     San Mateo         683.05         696.53   
5              Atwater city, CA        Merced        2939.20        2333.56   
6               Auburn city, CA        Placer        1036.24         971.99   
7              Belmont city, CA     San Mateo        2801.12        2815.62   
8            Belvedere city, CA         Marin         265.58         268.32   
9              Benicia city, CA        Solano        3106.75        3118.50   
10            Berkeley city, CA       Alameda       13564.56       13631.06   
11           Brentwood city, CA  Contra Costa        4304.24        4332.44   
12            Brisbane city, CA     San Mateo         556.60         559.72   
13          Burlingame city, CA     San Mateo        3038.48        2771.84   
14           Calistoga city, CA          Napa         559.81         560.56   
15            Campbell city, CA   Santa Clara        3878.36        3678.68   
16            Capitola city, CA    Santa Cruz        1730.87        1558.23   
17   Carmel-by-the-Sea city, CA      Monterey         495.51         526.42   
18               Ceres city, CA    Stanislaus        2714.35        2633.29   
19      Citrus Heights city, CA    Sacramento       10095.92        8053.11   
20             Clayton city, CA  Contra Costa         680.25         709.31   
21          Cloverdale city, CA        Sonoma         671.03         675.91   
22              Clovis city, CA        Fresno        5699.97        5786.72   
23            Coalinga city, CA        Fresno        1304.12        1281.75   
24              Colfax city, CA        Placer         157.90         148.11   
25               Colma town, CA     San Mateo         154.10         156.60   
26             Concord city, CA  Contra Costa       10405.57       10431.08   
27        Corte Madera town, CA         Marin        1029.14        1039.74   
28              Cotati city, CA        Sonoma         681.01         685.38   
29           Cupertino city, CA   Santa Clara        2726.44        2770.94   
..                          ...           ...            ...            ...   
168    Unincorporated_El Dorado     El Dorado       10293.64       10853.91   
169       Unincorporated_Fresno        Fresno       17231.95       16714.47   
170        Unincorporated_Marin         Marin        7444.78        7466.30   
171    Unincorporated_Mendocino     Mendocino        7730.93        6680.63   
172       Unincorporated_Merced        Merced        7638.02        6780.91   
173     Unincorporated_Monterey      Monterey        8179.80        8929.80   
174         Unincorporated_Napa          Napa        3014.66        3021.04   
175       Unincorporated_Placer        Placer        9410.19        8914.45   
176   Unincorporated_Sacramento    Sacramento       65332.28       63795.78   
177  Unincorporated_San Joaquin   San Joaquin       12404.38       10719.97   
178    Unincorporated_San Mateo     San Mateo        5444.94        5275.15   
179  Unincorporated_Santa Clara   Santa Clara        7074.21        7623.26   
180   Unincorporated_Santa Cruz    Santa Cruz       16621.55       16347.84   
181       Unincorporated_Solano        Solano        1839.02        1842.27   
182       Unincorporated_Sonoma        Sonoma       14333.14       14348.89   
183   Unincorporated_Stanislaus    Stanislaus        8998.61        8222.69   
184         Unincorporated_Yolo          Yolo        2259.38        2344.16   
185         Union City city, CA       Alameda        3976.43        4016.05   
186          Vacaville city, CA        Solano        8382.37        8418.24 

## Part B1. Organize Counties by Climate Zone

In [184]:
#import county climate zones
col = ["Zone","NAME","Area"]
county_df=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/Census Tiger Shapefiles/county_climate_zones.csv", delimiter=",",usecols = col)
county_df

Zone             NAME          Area
0       1           Sonoma 1320443466.00
1       1            Marin     101400.63
2       1        Mendocino 4227922351.00
3       1         Humboldt 8868963688.00
4       1        Del Norte 1328149857.00
5      10      Los Angeles     360132.43
6      10        San Diego 4109298922.00
7      10   San Bernardino 1819924221.00
8      10        Riverside 5794820947.00
9      10           Orange    2509331.60
10     11           Sierra    5035646.80
11     11       Sacramento     400259.99
12     11           Placer 2156313848.00
13     11           Shasta 8147445946.00
14     11          Trinity     848653.60
15     11        El Dorado     400941.00
16     11             Yolo    2608981.75
17     11             Yuba 2208046193.00
18     11           Colusa 4989136364.00
19     11           Tehama 8475737818.00
20     11           Nevada 1830990732.00
21     11            Butte 5420322851.00
22     11           Sutter 2613698578.00
23     11             Lake    2732140.45
24     11            Glenn 4268169989.00
25     12       Sacramento 4204866722.00
26     12        Calaveras 3445247653.00
27     12           Placer   11730050.35
28     12         Mariposa 3187176254.00
29     12             Napa    1973712.21
..    ...              ...           ...
141     4       Stanislaus    6772629.87
142     4        San Mateo     462368.86
143     4       Santa Cruz   15031170.68
144     4  San Luis Obispo 9626174958.00
145     5    Santa Barbara 8507149240.00
146     5          Ventura     329506.01
147     5         Monterey       7513.38
148     5  San Luis Obispo 3338633192.00
149     6    Santa Barbara  623640559.60
150     6          Ventura 1077085429.00
151     6      Los Angeles 1249271674.00
152     6        San Diego     312851.63
153     6           Orange  757723982.10
154     7        San Diego 2631041996.00
155     7        Riverside      87128.91
156     7           Orange      47533.74
157     8      Los Angeles  842238480.60
158     8        San Diego     465714.82
159     8   San Bernardino     293366.78
160     8        Riverside    2295388.17
161     8           Orange 2229220280.00
162     9    Santa Barbara      86695.07
163     9          Ventura 2097411696.00
164     9      Los Angeles 4054800922.00
165     9   San Bernardino     107757.84
166     9           Orange     561230.54
167     8      Los Angeles       6862.22
168     9      Los Angeles       6862.22
169     8           Orange       9447.56
170     9           Orange       9447.56

[171 rows x 3 columns]

In [185]:
#Sort by county and area of zone
sorted_counties = county_df.sort_values(by=['NAME', 'Area'],ascending=False)
sorted_counties

Zone          NAME           Area
17     11          Yuba  2208046193.00
87     16          Yuba   578664689.40
34     12          Yolo  4346246958.00
111     2          Yolo     8445144.04
16     11          Yolo     2608981.75
73     16       Ventura  3830753013.00
163     9       Ventura  2097411696.00
150     6       Ventura  1077085429.00
146     5       Ventura      329506.01
48     13       Ventura      282549.16
131     4       Ventura        1045.60
83     16      Tuolumne  7437043914.00
30     12      Tuolumne  2072334300.00
57     13        Tulare  9652884586.00
99     16        Tulare  9641977736.00
79     16       Trinity 12022051360.00
108     2       Trinity  2425474787.00
14     11       Trinity      848653.60
19     11        Tehama  8475737818.00
96     16        Tehama  4661640190.00
22     11        Sutter  2613698578.00
44     12        Sutter     1972277.90
43     12    Stanislaus  6243743836.00
141     4    Stanislaus     6772629.87
105     2        Sonoma  5418399326.00
0       1        Sonoma  1320443466.00
117     3        Sonoma      280211.10
31     12        Solano  3443686565.00
122     3        Solano   144998818.70
110     2        Solano      973284.51
..    ...           ...            ...
112     2      Humboldt  6680683651.00
88     16      Humboldt   614315560.70
24     11         Glenn  4268169989.00
104    16         Glenn  1527423810.00
116     2         Glenn      503943.77
54     13        Fresno 15373884329.00
94     16        Fresno  8926333977.00
136     4        Fresno     2060431.29
37     12        Fresno      603251.46
86     16     El Dorado  5069178738.00
33     12     El Dorado  2554547209.00
15     11     El Dorado      400941.00
92     16     Del Norte  3390045908.00
4       1     Del Norte  1328149857.00
32     12  Contra Costa  2869769930.00
123     3  Contra Costa   255386743.20
18     11        Colusa  4989136364.00
113     2        Colusa     1431081.95
36     12        Colusa      185312.00
91     16        Colusa       38819.27
26     12     Calaveras  3445247653.00
72     16     Calaveras   910965648.80
21     11         Butte  5420322851.00
98     16         Butte  1919712037.00
45     12        Amador  1694388902.00
100    16        Amador   868139009.40
85     16        Alpine  3156005675.00
41     12       Alameda  1677185786.00
126     3       Alameda  1401450134.00
139     4       Alameda     1004136.91

[171 rows x 3 columns]

In [186]:
#keep only largest zone per county
county_zones = sorted_counties.drop_duplicates(subset="NAME",keep="first")

In [187]:
#rename Zone variable and add "Unincorporated_" to County Names
county_climate_zones = county_zones[["Zone","NAME"]].copy()
county_climate_zones.NAME = "Unincorporated_" + county_climate_zones.NAME
county_climate_zones.rename(columns={"Zone":"Climate Zone"},inplace = True)
county_climate_zones

Climate Zone                            NAME
17             11             Unincorporated_Yuba
34             12             Unincorporated_Yolo
73             16          Unincorporated_Ventura
83             16         Unincorporated_Tuolumne
57             13           Unincorporated_Tulare
79             16          Unincorporated_Trinity
19             11           Unincorporated_Tehama
22             11           Unincorporated_Sutter
43             12       Unincorporated_Stanislaus
105             2           Unincorporated_Sonoma
31             12           Unincorporated_Solano
103            16         Unincorporated_Siskiyou
70             16           Unincorporated_Sierra
78             16           Unincorporated_Shasta
128             3       Unincorporated_Santa Cruz
137             4      Unincorporated_Santa Clara
145             5    Unincorporated_Santa Barbara
127             3        Unincorporated_San Mateo
144             4  Unincorporated_San Luis Obispo
40             12      Unincorporated_San Joaquin
118             3    Unincorporated_San Francisco
60             14        Unincorporated_San Diego
62             14   Unincorporated_San Bernardino
134             4       Unincorporated_San Benito
25             12       Unincorporated_Sacramento
68             15        Unincorporated_Riverside
102            16           Unincorporated_Plumas
75             16           Unincorporated_Placer
161             8           Unincorporated_Orange
97             16           Unincorporated_Nevada
107             2             Unincorporated_Napa
133             4         Unincorporated_Monterey
82             16             Unincorporated_Mono
93             16            Unincorporated_Modoc
42             12           Unincorporated_Merced
109             2        Unincorporated_Mendocino
28             12         Unincorporated_Mariposa
119             3            Unincorporated_Marin
55             13           Unincorporated_Madera
59             14      Unincorporated_Los Angeles
77             16           Unincorporated_Lassen
114             2             Unincorporated_Lake
49             13            Unincorporated_Kings
53             13             Unincorporated_Kern
81             16             Unincorporated_Inyo
69             15         Unincorporated_Imperial
3               1         Unincorporated_Humboldt
24             11            Unincorporated_Glenn
54             13           Unincorporated_Fresno
86             16        Unincorporated_El Dorado
92             16        Unincorporated_Del Norte
32             12     Unincorporated_Contra Costa
18             11           Unincorporated_Colusa
26             12        Unincorporated_Calaveras
21             11            Unincorporated_Butte
45             12           Unincorporated_Amador
85             16           Unincorporated_Alpine
41             12          Unincorporated_Alameda

## Part B2. Organize Cities by Climate Zone

In [188]:
#import city climate zones
col = ["Zone","NAMELSAD","Area"]
city_df=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/Census Tiger Shapefiles/city_climate_zones2.csv", delimiter=",", usecols=col)
city_df

Zone                      NAMELSAD        Area
0        1              Point Arena city  5567222.59
1        1            Crescent City city  9130277.76
2        1                Blue Lake city  2821557.53
3        1                  Fortuna city 21781328.01
4        1                 Rio Dell city 10836806.03
5        1                 Trinidad city  2011183.30
6        1                 Ferndale city  4614286.30
7        1                   Arcata city 42044478.43
8        1                   Eureka city 43447231.04
9        1               Fort Bragg city 11884193.42
10       1                    Albion CDP  7943814.92
11       1                Anchor Bay CDP 14871422.69
12       1                   Bayview CDP  3307524.28
13       1         Bertsch-Oceanview CDP 24560442.59
14       1                Big Lagoon CDP  2709031.77
15       1                    Bodega CDP 12238935.80
16       1                Bodega Bay CDP 35258497.90
17       1                    Carmet CDP  1209364.42
18       1                    Caspar CDP 12887228.27
19       1                  Cazadero CDP 30166678.89
20       1                    Cleone CDP  6890368.21
21       1                  Comptche CDP  4990799.59
22       1                    Cutten CDP  5848409.02
23       1                 Fairhaven CDP  2818773.66
24       1                Fieldbrook CDP 47620920.82
25       1            Fields Landing CDP  1249064.75
26       1                 Fort Dick CDP 15034771.02
27       1               Guerneville CDP  7116028.90
28       1                   Hiouchi CDP  1751272.69
29       1             Humboldt Hill CDP 18821814.78
...    ...                           ...         ...
1728     9     La Crescenta-Montrose CDP 11605427.51
1729     9             Lake Sherwood CDP 12686514.10
1730     9         Mayflower Village CDP  2605746.78
1731     9                Mira Monte CDP 15365303.90
1732     9            North El Monte CDP  1603102.11
1733     9                  Oak Park CDP 20075000.84
1734     9                  Oak View CDP  7481193.76
1735     9                      Piru CDP 10813990.62
1736     9                Rose Hills CDP  1628147.70
1737     9           Rowland Heights CDP 49221592.62
1738     9       San Antonio Heights CDP     2436.16
1739     9               San Pasqual CDP   966837.85
1740     9         Santa Rosa Valley CDP 24128626.69
1741     9              Santa Susana CDP  4231056.35
1742     9                   Saticoy CDP   427476.36
1743     9     South Monrovia Island CDP  2078242.28
1744     9         South San Gabriel CDP  3151628.50
1745     9      South San Jose Hills CDP  5698316.04
1746     9            South Whittier CDP 20164502.60
1747     9           Stevenson Ranch CDP 24239177.93
1748     9                   Topanga CDP 14181060.95
1749     9                   Valinda CDP  7616290.31
1750     9                 Val Verde CDP  9794705.91
1751     9                   Vincent CDP  5575045.30
1752     9        West Puente Valley CDP  7072747.28
1753     9  West Whittier-Los Nietos CDP  9511583.35
1754     8                La Mirada city     6862.22
1755     9                La Mirada city     6862.22
1756     8               Buena Park city     9447.56
1757     9               Buena Park city     9447.56

[1758 rows x 3 columns]

In [189]:
#Sort by name and zone area
sorted_cities = city_df.sort_values(by=['NAMELSAD', 'Area'],ascending=False)
sorted_cities

Zone             NAMELSAD         Area
1371     3          Zayante CDP  11112333.37
708     14    Yucca Valley town 151608261.00
106     10         Yucaipa city 103757024.70
863     16         Yucaipa city   3583912.40
177     11       Yuba City city  64676521.29
859     16           Yreka city  46807992.54
1145     2      Yountville city   6466982.77
1126    16  Yosemite Valley CDP   8797960.14
697     13   Yosemite Lakes CDP  85851211.00
1624     8     Yorba Linda city  74773799.82
86      10     Yorba Linda city     70966.50
540     12             Yolo CDP   5883158.03
696     13           Yettem CDP    616221.33
279     11      Yankee Hill CDP  26401400.70
1125    16       Wrightwood CDP  22584343.85
695     13        Woodville CDP  17294654.31
1254     3        Woodside town  48257105.99
1464     5        Woodlands CDP   6397238.47
342     12        Woodland city  65131374.86
577     13        Woodlake city  11409112.17
160     10        Woodcrest CDP  42862244.76
539     12       Woodbridge CDP  13092597.21
1222     2         Woodacre CDP   7506784.43
1124    16  Wofford Heights CDP  25200193.40
538     12           Winton CDP  12496992.16
341     12         Winters city  12546057.30
817     15      Winterhaven CDP    894243.34
159     10   Winter Gardens CDP  16298169.65
1150     2         Windsor town  30921970.99
158     10       Winchester CDP  30271538.70
...    ...                  ...          ...
1515     6     Alondra Park CDP     24694.94
869     16          Almanor CDP   3927623.68
579     13      Allensworth CDP  12255946.42
357     12        Allendale CDP  26215848.86
868     16        Alleghany CDP   1518453.25
1492     6     Aliso Viejo city  24516623.68
1597     8     Aliso Viejo city   1370688.43
1683     9        Alhambra city  28888098.23
356     12  Alhambra Valley CDP   5549260.96
1153     2       Alderpoint CDP  10778932.93
10       1           Albion CDP   7943814.92
1279     3          Albany city   7465985.54
355     12            Alamo CDP  40237314.79
1278     3         Alameda city  44232493.09
354     12          Airport CDP   2461988.94
578     13         Ahwahnee CDP  40623615.26
867     16         Ahwahnee CDP    548703.81
107     10          Aguanga CDP  48592994.88
784     15          Aguanga CDP   1977074.92
711     14          Aguanga CDP    160775.33
1714     9       Agua Dulce CDP  36761867.11
866     16       Agua Dulce CDP  27706151.61
710     14       Agua Dulce CDP  22907712.52
1698     9    Agoura Hills city  29656212.38
865     16             Adin CDP  15764286.65
701     14        Adelanto city 202988292.60
709     14            Acton CDP 149322093.20
864     16            Acton CDP    821807.63
353     12           Acampo CDP   3935714.11
352     12   Acalanes Ridge CDP   1919532.10

[1758 rows x 3 columns]

In [190]:
#keep only largest zone in city
city_zones = sorted_cities.drop_duplicates(subset="NAMELSAD",keep="first")
city_zones

Zone             NAMELSAD         Area
1371     3          Zayante CDP  11112333.37
708     14    Yucca Valley town 151608261.00
106     10         Yucaipa city 103757024.70
177     11       Yuba City city  64676521.29
859     16           Yreka city  46807992.54
1145     2      Yountville city   6466982.77
1126    16  Yosemite Valley CDP   8797960.14
697     13   Yosemite Lakes CDP  85851211.00
1624     8     Yorba Linda city  74773799.82
540     12             Yolo CDP   5883158.03
696     13           Yettem CDP    616221.33
279     11      Yankee Hill CDP  26401400.70
1125    16       Wrightwood CDP  22584343.85
695     13        Woodville CDP  17294654.31
1254     3        Woodside town  48257105.99
1464     5        Woodlands CDP   6397238.47
342     12        Woodland city  65131374.86
577     13        Woodlake city  11409112.17
160     10        Woodcrest CDP  42862244.76
539     12       Woodbridge CDP  13092597.21
1222     2         Woodacre CDP   7506784.43
1124    16  Wofford Heights CDP  25200193.40
538     12           Winton CDP  12496992.16
341     12         Winters city  12546057.30
817     15      Winterhaven CDP    894243.34
159     10   Winter Gardens CDP  16298169.65
1150     2         Windsor town  30921970.99
158     10       Winchester CDP  30271538.70
537     12           Wilton CDP 122536322.60
1123    16         Wilsonia CDP   1101059.90
...    ...                  ...          ...
1287     3             Alto CDP    524009.39
1715     9         Altadena CDP  22904262.14
190     11      Alta Sierra CDP  35946454.29
871     16             Alta CDP  10326687.73
870     16   Alpine Village CDP  11969516.90
108     10           Alpine CDP  58462715.55
580     13          Alpaugh CDP   3974245.71
1627     8     Alondra Park CDP   4281445.21
869     16          Almanor CDP   3927623.68
579     13      Allensworth CDP  12255946.42
357     12        Allendale CDP  26215848.86
868     16        Alleghany CDP   1518453.25
1492     6     Aliso Viejo city  24516623.68
1683     9        Alhambra city  28888098.23
356     12  Alhambra Valley CDP   5549260.96
1153     2       Alderpoint CDP  10778932.93
10       1           Albion CDP   7943814.92
1279     3          Albany city   7465985.54
355     12            Alamo CDP  40237314.79
1278     3         Alameda city  44232493.09
354     12          Airport CDP   2461988.94
578     13         Ahwahnee CDP  40623615.26
107     10          Aguanga CDP  48592994.88
1714     9       Agua Dulce CDP  36761867.11
1698     9    Agoura Hills city  29656212.38
865     16             Adin CDP  15764286.65
701     14        Adelanto city 202988292.60
709     14            Acton CDP 149322093.20
353     12           Acampo CDP   3935714.11
352     12   Acalanes Ridge CDP   1919532.10

[1511 rows x 3 columns]

In [191]:
#drop extra columns, rename Zone variable, and add ", CA" to city names
city_climate_zones = city_zones[["Zone","NAMELSAD"]].copy()
city_climate_zones.NAMELSAD = city_climate_zones.NAMELSAD + ", CA"
city_climate_zones.rename(columns={"NAMELSAD": "NAME","Zone":"Climate Zone"},inplace = True)
city_climate_zones

Climate Zone                     NAME
1371             3          Zayante CDP, CA
708             14    Yucca Valley town, CA
106             10         Yucaipa city, CA
177             11       Yuba City city, CA
859             16           Yreka city, CA
1145             2      Yountville city, CA
1126            16  Yosemite Valley CDP, CA
697             13   Yosemite Lakes CDP, CA
1624             8     Yorba Linda city, CA
540             12             Yolo CDP, CA
696             13           Yettem CDP, CA
279             11      Yankee Hill CDP, CA
1125            16       Wrightwood CDP, CA
695             13        Woodville CDP, CA
1254             3        Woodside town, CA
1464             5        Woodlands CDP, CA
342             12        Woodland city, CA
577             13        Woodlake city, CA
160             10        Woodcrest CDP, CA
539             12       Woodbridge CDP, CA
1222             2         Woodacre CDP, CA
1124            16  Wofford Heights CDP, CA
538             12           Winton CDP, CA
341             12         Winters city, CA
817             15      Winterhaven CDP, CA
159             10   Winter Gardens CDP, CA
1150             2         Windsor town, CA
158             10       Winchester CDP, CA
537             12           Wilton CDP, CA
1123            16         Wilsonia CDP, CA
...            ...                      ...
1287             3             Alto CDP, CA
1715             9         Altadena CDP, CA
190             11      Alta Sierra CDP, CA
871             16             Alta CDP, CA
870             16   Alpine Village CDP, CA
108             10           Alpine CDP, CA
580             13          Alpaugh CDP, CA
1627             8     Alondra Park CDP, CA
869             16          Almanor CDP, CA
579             13      Allensworth CDP, CA
357             12        Allendale CDP, CA
868             16        Alleghany CDP, CA
1492             6     Aliso Viejo city, CA
1683             9        Alhambra city, CA
356             12  Alhambra Valley CDP, CA
1153             2       Alderpoint CDP, CA
10               1           Albion CDP, CA
1279             3          Albany city, CA
355             12            Alamo CDP, CA
1278             3         Alameda city, CA
354             12          Airport CDP, CA
578             13         Ahwahnee CDP, CA
107             10          Aguanga CDP, CA
1714             9       Agua Dulce CDP, CA
1698             9    Agoura Hills city, CA
865             16             Adin CDP, CA
701             14        Adelanto city, CA
709             14            Acton CDP, CA
353             12           Acampo CDP, CA
352             12   Acalanes Ridge CDP, CA

[1511 rows x 2 columns]

In [192]:
#concatenate city and county dfs together
frames = [county_climate_zones,city_climate_zones]
climate_zones=pd.concat(frames,sort=True)
climate_zones

Climate Zone                            NAME
17              11             Unincorporated_Yuba
34              12             Unincorporated_Yolo
73              16          Unincorporated_Ventura
83              16         Unincorporated_Tuolumne
57              13           Unincorporated_Tulare
79              16          Unincorporated_Trinity
19              11           Unincorporated_Tehama
22              11           Unincorporated_Sutter
43              12       Unincorporated_Stanislaus
105              2           Unincorporated_Sonoma
31              12           Unincorporated_Solano
103             16         Unincorporated_Siskiyou
70              16           Unincorporated_Sierra
78              16           Unincorporated_Shasta
128              3       Unincorporated_Santa Cruz
137              4      Unincorporated_Santa Clara
145              5    Unincorporated_Santa Barbara
127              3        Unincorporated_San Mateo
144              4  Unincorporated_San Luis Obispo
40              12      Unincorporated_San Joaquin
118              3    Unincorporated_San Francisco
60              14        Unincorporated_San Diego
62              14   Unincorporated_San Bernardino
134              4       Unincorporated_San Benito
25              12       Unincorporated_Sacramento
68              15        Unincorporated_Riverside
102             16           Unincorporated_Plumas
75              16           Unincorporated_Placer
161              8           Unincorporated_Orange
97              16           Unincorporated_Nevada
...            ...                             ...
1287             3                    Alto CDP, CA
1715             9                Altadena CDP, CA
190             11             Alta Sierra CDP, CA
871             16                    Alta CDP, CA
870             16          Alpine Village CDP, CA
108             10                  Alpine CDP, CA
580             13                 Alpaugh CDP, CA
1627             8            Alondra Park CDP, CA
869             16                 Almanor CDP, CA
579             13             Allensworth CDP, CA
357             12               Allendale CDP, CA
868             16               Alleghany CDP, CA
1492             6            Aliso Viejo city, CA
1683             9               Alhambra city, CA
356             12         Alhambra Valley CDP, CA
1153             2              Alderpoint CDP, CA
10               1                  Albion CDP, CA
1279             3                 Albany city, CA
355             12                   Alamo CDP, CA
1278             3                Alameda city, CA
354             12                 Airport CDP, CA
578             13                Ahwahnee CDP, CA
107             10                 Aguanga CDP, CA
1714             9              Agua Dulce CDP, CA
1698             9           Agoura Hills city, CA
865             16                    Adin CDP, CA
701             14               Adelanto city, CA
709             14                   Acton CDP, CA
353             12                  Acampo CDP, CA
352             12          Acalanes Ridge CDP, CA

[1569 rows x 2 columns]

## Part B3. Incorporate Electricity Usage by Zone and Emissions Factors

In [193]:
electric_usage=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/CA Building Climate Zone Areas/electric_usage.csv", delimiter=",")
electric_usage

Climate Zone  Average Monthly Electricity Consumption (kWh)
0             1                                         626.41
1             2                                         642.02
2             3                                         420.48
3             4                                         531.39
4             5                                         446.10
5            11                                         816.21
6            12                                         713.87
7            13                                         767.26
8            16                                         473.11

In [194]:
hh_electric_use = climate_zones.merge(electric_usage, how="left", on="Climate Zone")
hh_electric_use.rename(columns={"NAME": "Place"},inplace = True)
hh_electric_use

Climate Zone                           Place  \
0               11             Unincorporated_Yuba   
1               12             Unincorporated_Yolo   
2               16          Unincorporated_Ventura   
3               16         Unincorporated_Tuolumne   
4               13           Unincorporated_Tulare   
5               16          Unincorporated_Trinity   
6               11           Unincorporated_Tehama   
7               11           Unincorporated_Sutter   
8               12       Unincorporated_Stanislaus   
9                2           Unincorporated_Sonoma   
10              12           Unincorporated_Solano   
11              16         Unincorporated_Siskiyou   
12              16           Unincorporated_Sierra   
13              16           Unincorporated_Shasta   
14               3       Unincorporated_Santa Cruz   
15               4      Unincorporated_Santa Clara   
16               5    Unincorporated_Santa Barbara   
17               3        Unincorporated_San Mateo   
18               4  Unincorporated_San Luis Obispo   
19              12      Unincorporated_San Joaquin   
20               3    Unincorporated_San Francisco   
21              14        Unincorporated_San Diego   
22              14   Unincorporated_San Bernardino   
23               4       Unincorporated_San Benito   
24              12       Unincorporated_Sacramento   
25              15        Unincorporated_Riverside   
26              16           Unincorporated_Plumas   
27              16           Unincorporated_Placer   
28               8           Unincorporated_Orange   
29              16           Unincorporated_Nevada   
...            ...                             ...   
1539             3                    Alto CDP, CA   
1540             9                Altadena CDP, CA   
1541            11             Alta Sierra CDP, CA   
1542            16                    Alta CDP, CA   
1543            16          Alpine Village CDP, CA   
1544            10                  Alpine CDP, CA   
1545            13                 Alpaugh CDP, CA   
1546             8            Alondra Park CDP, CA   
1547            16                 Almanor CDP, CA   
1548            13             Allensworth CDP, CA   
1549            12               Allendale CDP, CA   
1550            16               Alleghany CDP, CA   
1551             6            Aliso Viejo city, CA   
1552             9               Alhambra city, CA   
1553            12         Alhambra Valley CDP, CA   
1554             2              Alderpoint CDP, CA   
1555             1                  Albion CDP, CA   
1556             3                 Albany city, CA   
1557            12                   Alamo CDP, CA   
1558             3                Alameda city, CA   
1559            12                 Airport CDP, CA   
1560            13                Ahwahnee CDP, CA   
1561            10                 Aguanga CDP, CA   
1562             9              Agua Dulce CDP, CA   
1563             9           Agoura Hills city, CA   
1564            16                    Adin CDP, CA   
1565            14               Adelanto city, CA   
1566            14                   Acton CDP, CA   
1567            12                  Acampo CDP, CA   
1568            12          Acalanes Ridge CDP, CA   

      Average Monthly Electricity Consumption (kWh)  
0                                            816.21  
1                                            713.87  
2                                            473.11  
3                                            473.11  
4                                            767.26  
5                                            473.11  
6                                            816.21  
7                                            816.21  
8                                            713.87  
9                                            642.02  
10                                           713.87  
11       

## Part B4. Calculate Electric Emissions from BAS Scenario

In [195]:
# merge with BAS table
bas_electric = bas_df[["Place",
    "14_HI_hh_count",
    "14_LI_hh_count",
    "14_MoI_hh_count",
    "14_VLI_hh_count",
    "15_HI_hh_count",
    "15_LI_hh_count",
    "15_MoI_hh_count",
    "15_VLI_hh_count",
    "16_HI_hh_count",
    "16_LI_hh_count",
    "16_MoI_hh_count",
    "16_VLI_hh_count",
    "17_HI_hh_count",
    "17_LI_hh_count",
    "17_MoI_hh_count",
    "17_VLI_hh_count",
    "18_HI_hh_count",
    "18_LI_hh_count",
    "18_MoI_hh_count",
    "18_VLI_hh_count",
    "PUMA",
    "County_x"]].copy()
bas_electric = bas_electric.merge(hh_electric_use,how="left",on="Place")
bas_electric

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [196]:
# calculate yearly electric usage
bas_electric["15_electric_usage"]=bas_electric["Average Monthly Electricity Consumption (kWh)"]*(bas_electric["15_VLI_hh_count"]+bas_electric["15_LI_hh_count"]+bas_electric["15_MoI_hh_count"]+bas_electric["15_HI_hh_count"])
bas_electric["16_electric_usage"]=bas_electric["Average Monthly Electricity Consumption (kWh)"]*(bas_electric["16_VLI_hh_count"]+bas_electric["16_LI_hh_count"]+bas_electric["16_MoI_hh_count"]+bas_electric["16_HI_hh_count"])
bas_electric["17_electric_usage"]=bas_electric["Average Monthly Electricity Consumption (kWh)"]*(bas_electric["17_VLI_hh_count"]+bas_electric["17_LI_hh_count"]+bas_electric["17_MoI_hh_count"]+bas_electric["17_HI_hh_count"])
bas_electric["18_electric_usage"]=bas_electric["Average Monthly Electricity Consumption (kWh)"]*(bas_electric["18_VLI_hh_count"]+bas_electric["18_LI_hh_count"]+bas_electric["18_MoI_hh_count"]+bas_electric["18_HI_hh_count"])
bas_electric

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [197]:
#import electric emissions factors by year
electric_emissions=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/CA Building Climate Zone Areas/emissions_factors.csv", delimiter=",",index_col = "Year")
electric_emissions

Emission Factor (lbs/MWh)
Year                           
2012                     444.62
2013                     427.27
2014                     434.92
2015                     404.51
2016                     293.67
2017                     210.44
2018                     206.29
2019                     206.29
2020                     206.29
2021                     206.29
2022                     206.29
2023                     206.29
2024                     206.29
2025                     206.29

In [198]:
#add yearly emissions factors to electricity usage df
bas_electric["2015_emission_factor"]=electric_emissions.loc[2015,"Emission Factor (lbs/MWh)"]
bas_electric["2016_emission_factor"]=electric_emissions.loc[2016,"Emission Factor (lbs/MWh)"]
bas_electric["2017_emission_factor"]=electric_emissions.loc[2017,"Emission Factor (lbs/MWh)"]
bas_electric["2018_emission_factor"]=electric_emissions.loc[2018,"Emission Factor (lbs/MWh)"]
bas_electric

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

In [199]:
# multiply electricity usage by emissions factors for each year, divide by 1000 to convert mwh to kwh
# and multiply by 0.000453592 to convert from lbs to metric tonnes
bas_electric["15_electric_ghg"]=(bas_electric["15_electric_usage"]*bas_electric["2015_emission_factor"]*12)*0.001*0.000453592
bas_electric["16_electric_ghg"]=(bas_electric["16_electric_usage"]*bas_electric["2016_emission_factor"]*12)*0.001*0.000453592
bas_electric["17_electric_ghg"]=(bas_electric["17_electric_usage"]*bas_electric["2017_emission_factor"]*12)*0.001*0.000453592
bas_electric["18_electric_ghg"]=(bas_electric["18_electric_usage"]*bas_electric["2018_emission_factor"]*12)*0.001*0.000453592
bas_electric

Place  14_HI_hh_count  14_LI_hh_count  \
0              Alameda city, CA        11871.58         3819.09   
1               Albany city, CA         3002.88          543.58   
2      American Canyon city, CA         2145.56          883.23   
3              Antioch city, CA         9563.33         6038.01   
4             Atherton town, CA         1292.32          330.06   
5              Atwater city, CA         2969.50         1615.80   
6               Auburn city, CA         2154.49          817.84   
7              Belmont city, CA         5225.26         1451.52   
8            Belvedere city, CA          501.17          157.55   
9              Benicia city, CA         3662.20         1545.60   
10            Berkeley city, CA        18757.12         3395.42   
11           Brentwood city, CA         6308.82         2287.07   
12            Brisbane city, CA          661.25          332.44   
13          Burlingame city, CA         6260.59         1887.39   
14           Calistoga city, CA          826.73          340.33   
15            Campbell city, CA         6821.61         2779.87   
16            Capitola city, CA         1928.06          815.26   
17   Carmel-by-the-Sea city, CA         1360.73          434.42   
18               Ceres city, CA         4080.41         2589.29   
19      Citrus Heights city, CA         9427.22         8179.57   
20             Clayton city, CA         1973.42          414.38   
21          Cloverdale city, CA         1336.60          440.36   
22              Clovis city, CA        18830.84         4022.22   
23            Coalinga city, CA         1077.06          869.80   
24              Colfax city, CA          328.30          124.62   
25               Colma town, CA          183.53           97.88   
26             Concord city, CA        17386.68         6218.00   
27        Corte Madera town, CA         1942.03          610.51   
28              Cotati city, CA         1195.33          490.97   
29           Cupertino city, CA        11457.08         2689.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        22896.66         7282.76   
169       Unincorporated_Fresno        18453.65         9815.83   
170        Unincorporated_Marin        12340.23         4722.67   
171    Unincorporated_Mendocino         8460.69         4717.82   
172       Unincorporated_Merced         8618.12         5278.60   
173     Unincorporated_Monterey        16840.94         6733.10   
174         Unincorporated_Napa         4448.58         1831.28   
175       Unincorporated_Placer        20365.63         7346.68   
176   Unincorporated_Sacramento        63205.69        40025.02   
177  Unincorporated_San Joaquin        15910.24         8347.86   
178    Unincorporated_San Mateo        11337.32         2976.73   
179  Unincorporated_Santa Clara        12836.38         4355.54   
180   Unincorporated_Santa Cruz        19204.60         9922.04   
181       Unincorporated_Solano         2632.31         1156.47   
182       Unincorporated_Sonoma        25859.39         9488.09   
183   Unincorporated_Stanislaus        12590.34         6427.55   
184         Unincorporated_Yolo         2878.85         1149.12   
185         Union City city, CA         8915.99         2092.27   
186          Vacaville city, CA        11643.79         4932.77   
187            Vallejo city, CA        14421.87         6098.56   
188       Walnut Creek city, CA        17049.86         3209.05   
189          Waterford city, CA         1020.61          445.61   
190        Watsonville city, CA         4636.25         2778.22   
191    West Sacramento city, CA         6400.30         2554.74   
192            Willits city, CA          548.75          305.99   
193            Windsor town, CA         3742.48         1233.01   
194            Winters city, CA          796.82          318.06   
195           Woodland city, CA         6785.86         2708.64   
196   

## Part B5. Calculate Electric Emissions from Needs Scenario

In [200]:
# merge with BAS table
needs_electric = needs_df[["Place",
    "15_HI_hh_mod",
    "15_LI_hh_mod",
    "15_MoI_hh_mod",
    "15_VLI_hh_mod",
    "16_HI_hh_mod",
    "16_LI_hh_mod",
    "16_MoI_hh_mod",
    "16_VLI_hh_mod",
    "17_HI_hh_mod",
    "17_LI_hh_mod",
    "17_MoI_hh_mod",
    "17_VLI_hh_mod",
    "18_HI_hh_mod",
    "18_LI_hh_mod",
    "18_MoI_hh_mod",
    "18_VLI_hh_mod",
    "County_x"]].copy()
needs_electric = needs_electric.merge(hh_electric_use,how="left",on="Place")
needs_electric

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
0              Alameda city, CA      13503.94       5555.39        7857.53   
1               Albany city, CA       3104.72        927.50        1374.20   
2      American Canyon city, CA       2403.45        906.44        1024.66   
3              Antioch city, CA      10636.05       7078.68        7670.68   
4             Atherton town, CA       1293.82        333.31         243.75   
5              Atwater city, CA       4068.25       2051.20        1535.12   
6               Auburn city, CA       2544.26        681.03         852.18   
7              Belmont city, CA       6054.70       1523.23        1152.31   
8            Belvedere city, CA        560.86        157.93         100.69   
9              Benicia city, CA       4829.00       1723.20        2216.60   
10            Berkeley city, CA      19457.62       5793.50        8583.80   
11           Brentwood city, CA       9385.28       2302.57        4761.68   
12            Brisbane city, CA        821.56        395.97         304.56   
13          Burlingame city, CA       6626.00       1905.39        1691.33   
14           Calistoga city, CA        926.10        349.27         392.53   
15            Campbell city, CA       7418.66       2797.12        3466.70   
16            Capitola city, CA        815.73        359.25          50.83   
17   Carmel-by-the-Sea city, CA       1742.16        481.71         450.62   
18               Ceres city, CA       6305.70       2133.04        2680.77   
19      Citrus Heights city, CA      11836.51       7814.18        6614.34   
20             Clayton city, CA       2423.82        453.27         979.97   
21          Cloverdale city, CA       1430.64        503.16         589.15   
22              Clovis city, CA      21794.80       5548.34        7023.62   
23            Coalinga city, CA       1266.02        873.65         874.08   
24              Colfax city, CA        387.70        103.78         129.86   
25               Colma town, CA        194.53        101.00         110.51   
26             Concord city, CA      22210.65       6438.88       11214.54   
27        Corte Madera town, CA       2173.35        612.14         389.87   
28              Cotati city, CA       1555.49        601.33         851.33   
29           Cupertino city, CA      12854.34       2715.59        3299.67   
..                          ...           ...           ...            ...   
168    Unincorporated_El Dorado      19956.44       3000.22        6386.34   
169       Unincorporated_Fresno      21269.52      10348.43       10233.10   
170        Unincorporated_Marin      14196.33       4726.67        3634.44   
171    Unincorporated_Mendocino       3834.85       2423.22        3498.81   
172       Unincorporated_Merced      10724.90       5676.56        4487.54   
173     Unincorporated_Monterey      22044.05       7372.59        6906.14   
174         Unincorporated_Napa       4983.30       1879.42        2113.48   
175       Unincorporated_Placer      23096.66       6116.82        7820.19   
176   Unincorporated_Sacramento      73278.77      31884.34       36533.96   
177  Unincorporated_San Joaquin      13665.12       7004.25        6871.86   
178    Unincorporated_San Mateo      11614.82       2989.60        2391.07   
179  Unincorporated_Santa Clara      13726.18       4357.16        5104.08   
180   Unincorporated_Santa Cruz      18047.76       6518.07        3039.31   
181       Unincorporated_Solano       3681.29       1185.21        1573.59   
182       Unincorporated_Sonoma      28479.06      10519.43       12464.20   
183   Unincorporated_Stanislaus      16279.40       5537.21        6709.14   
184         Unincorporated_Yolo        854.39        735.68         878.97   
185         Union City city, CA      13215.02       3124.74        5316.54   
186          Vacaville city, CA      16869.01       5115.73        6953.01   
187            Vallejo city, CA      19017.48   

In [201]:
# calculate yearly electric usage
needs_electric["15_electric_usage"]=needs_electric["Average Monthly Electricity Consumption (kWh)"]*(needs_electric["15_VLI_hh_mod"]+needs_electric["15_LI_hh_mod"]+needs_electric["15_MoI_hh_mod"]+needs_electric["15_HI_hh_mod"])
needs_electric["16_electric_usage"]=needs_electric["Average Monthly Electricity Consumption (kWh)"]*(needs_electric["16_VLI_hh_mod"]+needs_electric["16_LI_hh_mod"]+needs_electric["16_MoI_hh_mod"]+needs_electric["16_HI_hh_mod"])
needs_electric["17_electric_usage"]=needs_electric["Average Monthly Electricity Consumption (kWh)"]*(needs_electric["17_VLI_hh_mod"]+needs_electric["17_LI_hh_mod"]+needs_electric["17_MoI_hh_mod"]+needs_electric["17_HI_hh_mod"])
needs_electric["18_electric_usage"]=needs_electric["Average Monthly Electricity Consumption (kWh)"]*(needs_electric["18_VLI_hh_mod"]+needs_electric["18_LI_hh_mod"]+needs_electric["18_MoI_hh_mod"]+needs_electric["18_HI_hh_mod"])
needs_electric

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
0              Alameda city, CA      13503.94       5555.39        7857.53   
1               Albany city, CA       3104.72        927.50        1374.20   
2      American Canyon city, CA       2403.45        906.44        1024.66   
3              Antioch city, CA      10636.05       7078.68        7670.68   
4             Atherton town, CA       1293.82        333.31         243.75   
5              Atwater city, CA       4068.25       2051.20        1535.12   
6               Auburn city, CA       2544.26        681.03         852.18   
7              Belmont city, CA       6054.70       1523.23        1152.31   
8            Belvedere city, CA        560.86        157.93         100.69   
9              Benicia city, CA       4829.00       1723.20        2216.60   
10            Berkeley city, CA      19457.62       5793.50        8583.80   
11           Brentwood city, CA       9385.28       2302.57        4761.68   
12            Brisbane city, CA        821.56        395.97         304.56   
13          Burlingame city, CA       6626.00       1905.39        1691.33   
14           Calistoga city, CA        926.10        349.27         392.53   
15            Campbell city, CA       7418.66       2797.12        3466.70   
16            Capitola city, CA        815.73        359.25          50.83   
17   Carmel-by-the-Sea city, CA       1742.16        481.71         450.62   
18               Ceres city, CA       6305.70       2133.04        2680.77   
19      Citrus Heights city, CA      11836.51       7814.18        6614.34   
20             Clayton city, CA       2423.82        453.27         979.97   
21          Cloverdale city, CA       1430.64        503.16         589.15   
22              Clovis city, CA      21794.80       5548.34        7023.62   
23            Coalinga city, CA       1266.02        873.65         874.08   
24              Colfax city, CA        387.70        103.78         129.86   
25               Colma town, CA        194.53        101.00         110.51   
26             Concord city, CA      22210.65       6438.88       11214.54   
27        Corte Madera town, CA       2173.35        612.14         389.87   
28              Cotati city, CA       1555.49        601.33         851.33   
29           Cupertino city, CA      12854.34       2715.59        3299.67   
..                          ...           ...           ...            ...   
168    Unincorporated_El Dorado      19956.44       3000.22        6386.34   
169       Unincorporated_Fresno      21269.52      10348.43       10233.10   
170        Unincorporated_Marin      14196.33       4726.67        3634.44   
171    Unincorporated_Mendocino       3834.85       2423.22        3498.81   
172       Unincorporated_Merced      10724.90       5676.56        4487.54   
173     Unincorporated_Monterey      22044.05       7372.59        6906.14   
174         Unincorporated_Napa       4983.30       1879.42        2113.48   
175       Unincorporated_Placer      23096.66       6116.82        7820.19   
176   Unincorporated_Sacramento      73278.77      31884.34       36533.96   
177  Unincorporated_San Joaquin      13665.12       7004.25        6871.86   
178    Unincorporated_San Mateo      11614.82       2989.60        2391.07   
179  Unincorporated_Santa Clara      13726.18       4357.16        5104.08   
180   Unincorporated_Santa Cruz      18047.76       6518.07        3039.31   
181       Unincorporated_Solano       3681.29       1185.21        1573.59   
182       Unincorporated_Sonoma      28479.06      10519.43       12464.20   
183   Unincorporated_Stanislaus      16279.40       5537.21        6709.14   
184         Unincorporated_Yolo        854.39        735.68         878.97   
185         Union City city, CA      13215.02       3124.74        5316.54   
186          Vacaville city, CA      16869.01       5115.73        6953.01   
187            Vallejo city, CA      19017.48   

In [202]:
#add yearly emissions factors to electricity usage df
needs_electric["2015_emission_factor"]=electric_emissions.loc[2015,"Emission Factor (lbs/MWh)"]
needs_electric["2016_emission_factor"]=electric_emissions.loc[2016,"Emission Factor (lbs/MWh)"]
needs_electric["2017_emission_factor"]=electric_emissions.loc[2017,"Emission Factor (lbs/MWh)"]
needs_electric["2018_emission_factor"]=electric_emissions.loc[2018,"Emission Factor (lbs/MWh)"]
needs_electric

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
0              Alameda city, CA      13503.94       5555.39        7857.53   
1               Albany city, CA       3104.72        927.50        1374.20   
2      American Canyon city, CA       2403.45        906.44        1024.66   
3              Antioch city, CA      10636.05       7078.68        7670.68   
4             Atherton town, CA       1293.82        333.31         243.75   
5              Atwater city, CA       4068.25       2051.20        1535.12   
6               Auburn city, CA       2544.26        681.03         852.18   
7              Belmont city, CA       6054.70       1523.23        1152.31   
8            Belvedere city, CA        560.86        157.93         100.69   
9              Benicia city, CA       4829.00       1723.20        2216.60   
10            Berkeley city, CA      19457.62       5793.50        8583.80   
11           Brentwood city, CA       9385.28       2302.57        4761.68   
12            Brisbane city, CA        821.56        395.97         304.56   
13          Burlingame city, CA       6626.00       1905.39        1691.33   
14           Calistoga city, CA        926.10        349.27         392.53   
15            Campbell city, CA       7418.66       2797.12        3466.70   
16            Capitola city, CA        815.73        359.25          50.83   
17   Carmel-by-the-Sea city, CA       1742.16        481.71         450.62   
18               Ceres city, CA       6305.70       2133.04        2680.77   
19      Citrus Heights city, CA      11836.51       7814.18        6614.34   
20             Clayton city, CA       2423.82        453.27         979.97   
21          Cloverdale city, CA       1430.64        503.16         589.15   
22              Clovis city, CA      21794.80       5548.34        7023.62   
23            Coalinga city, CA       1266.02        873.65         874.08   
24              Colfax city, CA        387.70        103.78         129.86   
25               Colma town, CA        194.53        101.00         110.51   
26             Concord city, CA      22210.65       6438.88       11214.54   
27        Corte Madera town, CA       2173.35        612.14         389.87   
28              Cotati city, CA       1555.49        601.33         851.33   
29           Cupertino city, CA      12854.34       2715.59        3299.67   
..                          ...           ...           ...            ...   
168    Unincorporated_El Dorado      19956.44       3000.22        6386.34   
169       Unincorporated_Fresno      21269.52      10348.43       10233.10   
170        Unincorporated_Marin      14196.33       4726.67        3634.44   
171    Unincorporated_Mendocino       3834.85       2423.22        3498.81   
172       Unincorporated_Merced      10724.90       5676.56        4487.54   
173     Unincorporated_Monterey      22044.05       7372.59        6906.14   
174         Unincorporated_Napa       4983.30       1879.42        2113.48   
175       Unincorporated_Placer      23096.66       6116.82        7820.19   
176   Unincorporated_Sacramento      73278.77      31884.34       36533.96   
177  Unincorporated_San Joaquin      13665.12       7004.25        6871.86   
178    Unincorporated_San Mateo      11614.82       2989.60        2391.07   
179  Unincorporated_Santa Clara      13726.18       4357.16        5104.08   
180   Unincorporated_Santa Cruz      18047.76       6518.07        3039.31   
181       Unincorporated_Solano       3681.29       1185.21        1573.59   
182       Unincorporated_Sonoma      28479.06      10519.43       12464.20   
183   Unincorporated_Stanislaus      16279.40       5537.21        6709.14   
184         Unincorporated_Yolo        854.39        735.68         878.97   
185         Union City city, CA      13215.02       3124.74        5316.54   
186          Vacaville city, CA      16869.01       5115.73        6953.01   
187            Vallejo city, CA      19017.48   

In [203]:
# multiply electricity usage by emissions factors for each year, divide by 1000 to convert mwh to kwh
# and multiply by 0.000453592 to convert from lbs to metric tonnes
needs_electric["15_electric_ghg"]=(needs_electric["15_electric_usage"]*needs_electric["2015_emission_factor"]*12)*0.001*0.000453592
needs_electric["16_electric_ghg"]=(needs_electric["16_electric_usage"]*needs_electric["2016_emission_factor"]*12)*0.001*0.000453592
needs_electric["17_electric_ghg"]=(needs_electric["17_electric_usage"]*needs_electric["2017_emission_factor"]*12)*0.001*0.000453592
needs_electric["18_electric_ghg"]=(needs_electric["18_electric_usage"]*needs_electric["2018_emission_factor"]*12)*0.001*0.000453592
needs_electric

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
0              Alameda city, CA      13503.94       5555.39        7857.53   
1               Albany city, CA       3104.72        927.50        1374.20   
2      American Canyon city, CA       2403.45        906.44        1024.66   
3              Antioch city, CA      10636.05       7078.68        7670.68   
4             Atherton town, CA       1293.82        333.31         243.75   
5              Atwater city, CA       4068.25       2051.20        1535.12   
6               Auburn city, CA       2544.26        681.03         852.18   
7              Belmont city, CA       6054.70       1523.23        1152.31   
8            Belvedere city, CA        560.86        157.93         100.69   
9              Benicia city, CA       4829.00       1723.20        2216.60   
10            Berkeley city, CA      19457.62       5793.50        8583.80   
11           Brentwood city, CA       9385.28       2302.57        4761.68   
12            Brisbane city, CA        821.56        395.97         304.56   
13          Burlingame city, CA       6626.00       1905.39        1691.33   
14           Calistoga city, CA        926.10        349.27         392.53   
15            Campbell city, CA       7418.66       2797.12        3466.70   
16            Capitola city, CA        815.73        359.25          50.83   
17   Carmel-by-the-Sea city, CA       1742.16        481.71         450.62   
18               Ceres city, CA       6305.70       2133.04        2680.77   
19      Citrus Heights city, CA      11836.51       7814.18        6614.34   
20             Clayton city, CA       2423.82        453.27         979.97   
21          Cloverdale city, CA       1430.64        503.16         589.15   
22              Clovis city, CA      21794.80       5548.34        7023.62   
23            Coalinga city, CA       1266.02        873.65         874.08   
24              Colfax city, CA        387.70        103.78         129.86   
25               Colma town, CA        194.53        101.00         110.51   
26             Concord city, CA      22210.65       6438.88       11214.54   
27        Corte Madera town, CA       2173.35        612.14         389.87   
28              Cotati city, CA       1555.49        601.33         851.33   
29           Cupertino city, CA      12854.34       2715.59        3299.67   
..                          ...           ...           ...            ...   
168    Unincorporated_El Dorado      19956.44       3000.22        6386.34   
169       Unincorporated_Fresno      21269.52      10348.43       10233.10   
170        Unincorporated_Marin      14196.33       4726.67        3634.44   
171    Unincorporated_Mendocino       3834.85       2423.22        3498.81   
172       Unincorporated_Merced      10724.90       5676.56        4487.54   
173     Unincorporated_Monterey      22044.05       7372.59        6906.14   
174         Unincorporated_Napa       4983.30       1879.42        2113.48   
175       Unincorporated_Placer      23096.66       6116.82        7820.19   
176   Unincorporated_Sacramento      73278.77      31884.34       36533.96   
177  Unincorporated_San Joaquin      13665.12       7004.25        6871.86   
178    Unincorporated_San Mateo      11614.82       2989.60        2391.07   
179  Unincorporated_Santa Clara      13726.18       4357.16        5104.08   
180   Unincorporated_Santa Cruz      18047.76       6518.07        3039.31   
181       Unincorporated_Solano       3681.29       1185.21        1573.59   
182       Unincorporated_Sonoma      28479.06      10519.43       12464.20   
183   Unincorporated_Stanislaus      16279.40       5537.21        6709.14   
184         Unincorporated_Yolo        854.39        735.68         878.97   
185         Union City city, CA      13215.02       3124.74        5316.54   
186          Vacaville city, CA      16869.01       5115.73        6953.01   
187            Vallejo city, CA      19017.48   

## Part C1. Calculate Gas Usage for BAS Scenario

In [204]:
#import gas usage table
gas_usage=pd.read_csv("C:/Users/jonst/Box/Cost of Doing Nothing/Climate Impacts/Data/CA Building Climate Zone Areas/gas_usage.csv", delimiter=",")
gas_usage

Region  gas_usage  \
0  San Francisco and Mid Coast      35.50   
1               Central Valley      33.50   
2          North and Mountains      36.50   

                                            Counties  
0  Alameda, Contra Costa, Lake, Marin, Mendocino,...  
1  Fresno, Kern, Kings, Madera, Mariposa, Merced,...  
2  Alpine, Amador, Butte, Calaveras, Colusa, Del ...

In [205]:
#calulate gas usage for BAS scenario
bas_gas = bas_df[["Place",
    "15_HI_hh_count",
    "15_LI_hh_count",
    "15_MoI_hh_count",
    "15_VLI_hh_count",
    "16_HI_hh_count",
    "16_LI_hh_count",
    "16_MoI_hh_count",
    "16_VLI_hh_count",
    "17_HI_hh_count",
    "17_LI_hh_count",
    "17_MoI_hh_count",
    "17_VLI_hh_count",
    "18_HI_hh_count",
    "18_LI_hh_count",
    "18_MoI_hh_count",
    "18_VLI_hh_count",
    "PUMA",
    "County_x"]].copy()
bas_gas

Place  15_HI_hh_count  15_LI_hh_count  \
0              Alameda city, CA        11593.90         5555.39   
1               Albany city, CA         3056.84          927.50   
2      American Canyon city, CA         2319.08          906.44   
3              Antioch city, CA         9484.27         7078.68   
4             Atherton town, CA         1036.48          310.21   
5              Atwater city, CA         2765.50         2051.20   
6               Auburn city, CA         2071.44          681.03   
7              Belmont city, CA         6138.72         1523.23   
8            Belvedere city, CA          504.88          105.55   
9              Benicia city, CA         4020.40         1723.20   
10            Berkeley city, CA        19094.16         5793.50   
11           Brentwood city, CA         8331.29         1673.41   
12            Brisbane city, CA          732.64          395.97   
13          Burlingame city, CA         6212.11         1493.18   
14           Calistoga city, CA          893.59          349.27   
15            Campbell city, CA         7755.11         2163.67   
16            Capitola city, CA         1929.93          767.21   
17   Carmel-by-the-Sea city, CA         1477.75          481.71   
18               Ceres city, CA         5381.23         2133.04   
19      Citrus Heights city, CA         9295.04         7815.46   
20             Clayton city, CA         2067.03          453.27   
21          Cloverdale city, CA         1280.72          503.16   
22              Clovis city, CA        19249.99         5548.34   
23            Coalinga city, CA         1186.42          873.65   
24              Colfax city, CA          315.65          103.78   
25               Colma town, CA          201.55          101.00   
26             Concord city, CA        19338.47         6438.88   
27        Corte Madera town, CA         1956.41          409.01   
28              Cotati city, CA         1164.04          601.33   
29           Cupertino city, CA        13499.81         1956.71   
..                          ...             ...             ...   
168    Unincorporated_El Dorado        27111.89         5705.15   
169       Unincorporated_Fresno        19638.22        10348.43   
170        Unincorporated_Marin        13438.84         3596.33   
171    Unincorporated_Mendocino         8710.88         5007.56   
172       Unincorporated_Merced         8404.22         5676.56   
173     Unincorporated_Monterey        18636.21         7372.59   
174         Unincorporated_Napa         4808.38         1879.42   
175       Unincorporated_Placer        19680.46         6318.97   
176   Unincorporated_Sacramento        70755.62        34465.26   
177  Unincorporated_San Joaquin        16610.00         8786.51   
178    Unincorporated_San Mateo        10402.48         2894.34   
179  Unincorporated_Santa Clara        13577.06         4212.01   
180   Unincorporated_Santa Cruz        20248.15         8420.57   
181       Unincorporated_Solano         2854.39         1185.21   
182       Unincorporated_Sonoma        24910.51        10519.43   
183   Unincorporated_Stanislaus        14268.79         5537.21   
184         Unincorporated_Yolo         3329.20         1340.64   
185         Union City city, CA        10047.32         3124.74   
186          Vacaville city, CA        12823.27         5115.73   
187            Vallejo city, CA        15821.10         6785.02   
188       Walnut Creek city, CA        17601.11         3446.44   
189          Waterford city, CA         1106.69          395.38   
190        Watsonville city, CA         5106.00         2198.34   
191    West Sacramento city, CA         7401.52         2980.53   
192            Willits city, CA          564.98          324.78   
193            Windsor town, CA         3586.02         1408.85   
194            Winters city, CA          921.48          371.07   
195           Woodland city, CA         7847.40         3160.08   
196   

In [206]:
sf_midcoast_mask = (bas_gas["County_x"]=="Alameda")|(bas_gas["County_x"]=="Alameda")|(bas_gas["County_x"]=="Contra Costa")|(bas_gas["County_x"]=="Lake")|(bas_gas["County_x"]=="Marin")|(bas_gas["County_x"]=="Mendocino")|(bas_gas["County_x"]=="Monterey")|(bas_gas["County_x"]=="Napa")|(bas_gas["County_x"]=="San Benito")|(bas_gas["County_x"]=="San Francisco")|(bas_gas["County_x"]=="San Mateo")|(bas_gas["County_x"]=="Santa Clara")|(bas_gas["County_x"]=="Santa Cruz")|(bas_gas["County_x"]=="Solano")|(bas_gas["County_x"]=="Sonoma")
sf_midcoast_gas = bas_gas[sf_midcoast_mask].copy()
sf_midcoast_gas["gas_usage"]=35.5
sf_midcoast_gas

Place  15_HI_hh_count  15_LI_hh_count  \
0                Alameda city, CA        11593.90         5555.39   
1                 Albany city, CA         3056.84          927.50   
2        American Canyon city, CA         2319.08          906.44   
3                Antioch city, CA         9484.27         7078.68   
4               Atherton town, CA         1036.48          310.21   
7                Belmont city, CA         6138.72         1523.23   
8              Belvedere city, CA          504.88          105.55   
9                Benicia city, CA         4020.40         1723.20   
10              Berkeley city, CA        19094.16         5793.50   
11             Brentwood city, CA         8331.29         1673.41   
12              Brisbane city, CA          732.64          395.97   
13            Burlingame city, CA         6212.11         1493.18   
14             Calistoga city, CA          893.59          349.27   
15              Campbell city, CA         7755.11         2163.67   
16              Capitola city, CA         1929.93          767.21   
17     Carmel-by-the-Sea city, CA         1477.75          481.71   
20               Clayton city, CA         2067.03          453.27   
21            Cloverdale city, CA         1280.72          503.16   
25                 Colma town, CA          201.55          101.00   
26               Concord city, CA        19338.47         6438.88   
27          Corte Madera town, CA         1956.41          409.01   
28                Cotati city, CA         1164.04          601.33   
29             Cupertino city, CA        13499.81         1956.71   
30             Daly City city, CA        11672.34         5886.34   
31              Danville town, CA         9675.78         1168.85   
33          Del Rey Oaks city, CA          321.25          104.72   
34                 Dixon city, CA         2405.52          959.66   
36                Dublin city, CA         9882.77         1270.97   
37        East Palo Alto city, CA         3224.59          965.10   
38            El Cerrito city, CA         4291.45         1194.04   
..                            ...             ...             ...   
151              Seaside city, CA         4722.38         1539.38   
152           Sebastopol city, CA         1312.74          515.74   
154              Soledad city, CA         1437.01          757.77   
155               Sonoma city, CA         2081.17          817.63   
157  South San Francisco city, CA         8345.75         4510.59   
158           St. Helena city, CA         1085.08          424.12   
160          Suisun City city, CA         3507.58         1578.16   
161            Sunnyvale city, CA        28685.24         6753.77   
162              Tiburon town, CA         1956.41          409.01   
165                Ukiah city, CA         1799.55         1034.49   
166        Unincorporated_Alameda        19766.47         8670.08   
167   Unincorporated_Contra Costa        27743.06         7306.09   
170          Unincorporated_Marin        13438.84         3596.33   
171      Unincorporated_Mendocino         8710.88         5007.56   
173       Unincorporated_Monterey        18636.21         7372.59   
174           Unincorporated_Napa         4808.38         1879.42   
178      Unincorporated_San Mateo        10402.48         2894.34   
179    Unincorporated_Santa Clara        13577.06         4212.01   
180     Unincorporated_Santa Cruz        20248.15         8420.57   
181         Unincorporated_Solano         2854.39         1185.21   
182         Unincorporated_Sonoma        24910.51        10519.43   
185           Union City city, CA        10047.32         3124.74   
186            Vacaville city, CA        12823.27         5115.73   
187              Vallejo city, CA        15821.10         6785.02   
188         Walnut Creek city, CA        17601.11         3446.44   
190          Watsonville city, CA         5106.00         2198.34   
192              Willits c

In [207]:
central_valley_mask = (bas_gas["County_x"]=="Fresno")|(bas_gas["County_x"]=="Kern")|(bas_gas["County_x"]=="Kings")|(bas_gas["County_x"]=="Madera")|(bas_gas["County_x"]=="Mariposa")|(bas_gas["County_x"]=="Merced")|(bas_gas["County_x"]=="Tulare")|(bas_gas["County_x"]=="Tuolumne")
central_valley_gas = bas_gas[central_valley_mask].copy()
central_valley_gas["gas_usage"]=33.5
central_valley_gas

Place  15_HI_hh_count  15_LI_hh_count  15_MoI_hh_count  \
5         Atwater city, CA         2765.50         2051.20          1535.12   
22         Clovis city, CA        19249.99         5548.34          7023.62   
23       Coalinga city, CA         1186.42          873.65           874.08   
35      Dos Palos city, CA          534.89          332.47           276.42   
44      Firebaugh city, CA          576.58          424.58           424.79   
48         Fowler city, CA          498.96          367.43           367.61   
50         Fresno city, CA        60807.56        26071.65         26808.97   
55        Gustine city, CA          660.74          410.70           341.46   
63          Huron city, CA          432.43          318.44           318.59   
65         Kerman city, CA         1064.45          783.84           784.22   
67      Kingsburg city, CA         1336.61          641.55           587.59   
73     Livingston city, CA         1048.80          651.90           542.00   
78      Los Banos city, CA         3597.38         2236.02          1859.06   
83        Mendota city, CA          698.54          514.39           514.65   
85         Merced city, CA         7780.65         5771.00          4319.02   
102   Orange Cove city, CA          734.40          352.50           322.85   
107       Parlier city, CA         1145.66          549.90           503.65   
120       Reedley city, CA         2247.26         1078.65           987.92   
135   San Joaquin city, CA          255.02          187.79           187.89   
144        Sanger city, CA         2335.39         1120.95          1026.66   
153         Selma city, CA         1862.78         1371.72          1372.39   
169  Unincorporated_Fresno        19638.22        10348.43         10233.10   
172  Unincorporated_Merced         8404.22         5676.56          4487.54   

     15_VLI_hh_count  16_HI_hh_count  16_LI_hh_count  16_MoI_hh_count  \
5            2939.20         3160.38         1683.73          1706.70   
22           5699.97        19693.03         4875.43          5724.26   
23           1304.12         1182.56         1020.67           622.85   
35            419.17          525.10          400.86           254.59   
44            633.78          574.70          496.03           302.69   
48            548.46          497.34          429.25           261.94   
50          48959.44        62744.18        23858.15         25931.87   
55            517.80          648.65          495.18           314.50   
63            475.33          431.03          372.02           227.02   
65           1170.05         1060.99          915.74           558.82   
67           1045.59         1649.28          594.96           454.55   
73            821.90         1029.60          786.00           499.20   
78           2819.12         3531.53         2695.98          1712.26   
83            767.84          696.28          600.96           366.72   
85           8269.35         8891.62         4737.13          4801.75   
102           574.50          906.20          326.90           249.75   
107           896.22         1413.67          509.96           389.61   
120          1757.97         2772.97         1000.31           764.24   
135           280.32          254.20          219.40           133.88   
144          1826.91         2881.72         1039.54           794.21   
153          2047.58         1856.74         1602.55           977.93   
169         17231.95        21517.71        10374.43          8278.38   
172          7638.02         8857.46         5768.53          4532.17   

     16_VLI_hh_count  17_HI_hh_count  17_LI_hh_count  17_MoI_hh_count  \
5            2333.56         3276.56         1555.58          1530.10   
22           5786.72        20584.44         4555.65          5210.05   
23           1281.75         1478.63          850.33           852.04   
35            415.50          633.78          349.61           358.68   
44    

In [208]:
mountain_mask = (bas_gas["County_x"]=="Alpine")|(bas_gas["County_x"]=="Amador")|(bas_gas["County_x"]=="Butte")|(bas_gas["County_x"]=="Calaveras")|(bas_gas["County_x"]=="Colusa")|(bas_gas["County_x"]=="Del Norte")|(bas_gas["County_x"]=="El Dorado")|(bas_gas["County_x"]=="Glenn")|(bas_gas["County_x"]=="Humboldt")|(bas_gas["County_x"]=="Placer")|(bas_gas["County_x"]=="Sacramento")|(bas_gas["County_x"]=="San Joaquin")|(bas_gas["County_x"]=="Stanislaus")|(bas_gas["County_x"]=="Yolo")|(bas_gas["County_x"]=="Yuba")
mountain_gas = bas_gas[central_valley_mask].copy()
mountain_gas["gas_usage"]=36.5
mountain_gas

Place  15_HI_hh_count  15_LI_hh_count  15_MoI_hh_count  \
5         Atwater city, CA         2765.50         2051.20          1535.12   
22         Clovis city, CA        19249.99         5548.34          7023.62   
23       Coalinga city, CA         1186.42          873.65           874.08   
35      Dos Palos city, CA          534.89          332.47           276.42   
44      Firebaugh city, CA          576.58          424.58           424.79   
48         Fowler city, CA          498.96          367.43           367.61   
50         Fresno city, CA        60807.56        26071.65         26808.97   
55        Gustine city, CA          660.74          410.70           341.46   
63          Huron city, CA          432.43          318.44           318.59   
65         Kerman city, CA         1064.45          783.84           784.22   
67      Kingsburg city, CA         1336.61          641.55           587.59   
73     Livingston city, CA         1048.80          651.90           542.00   
78      Los Banos city, CA         3597.38         2236.02          1859.06   
83        Mendota city, CA          698.54          514.39           514.65   
85         Merced city, CA         7780.65         5771.00          4319.02   
102   Orange Cove city, CA          734.40          352.50           322.85   
107       Parlier city, CA         1145.66          549.90           503.65   
120       Reedley city, CA         2247.26         1078.65           987.92   
135   San Joaquin city, CA          255.02          187.79           187.89   
144        Sanger city, CA         2335.39         1120.95          1026.66   
153         Selma city, CA         1862.78         1371.72          1372.39   
169  Unincorporated_Fresno        19638.22        10348.43         10233.10   
172  Unincorporated_Merced         8404.22         5676.56          4487.54   

     15_VLI_hh_count  16_HI_hh_count  16_LI_hh_count  16_MoI_hh_count  \
5            2939.20         3160.38         1683.73          1706.70   
22           5699.97        19693.03         4875.43          5724.26   
23           1304.12         1182.56         1020.67           622.85   
35            419.17          525.10          400.86           254.59   
44            633.78          574.70          496.03           302.69   
48            548.46          497.34          429.25           261.94   
50          48959.44        62744.18        23858.15         25931.87   
55            517.80          648.65          495.18           314.50   
63            475.33          431.03          372.02           227.02   
65           1170.05         1060.99          915.74           558.82   
67           1045.59         1649.28          594.96           454.55   
73            821.90         1029.60          786.00           499.20   
78           2819.12         3531.53         2695.98          1712.26   
83            767.84          696.28          600.96           366.72   
85           8269.35         8891.62         4737.13          4801.75   
102           574.50          906.20          326.90           249.75   
107           896.22         1413.67          509.96           389.61   
120          1757.97         2772.97         1000.31           764.24   
135           280.32          254.20          219.40           133.88   
144          1826.91         2881.72         1039.54           794.21   
153          2047.58         1856.74         1602.55           977.93   
169         17231.95        21517.71        10374.43          8278.38   
172          7638.02         8857.46         5768.53          4532.17   

     16_VLI_hh_count  17_HI_hh_count  17_LI_hh_count  17_MoI_hh_count  \
5            2333.56         3276.56         1555.58          1530.10   
22           5786.72        20584.44         4555.65          5210.05   
23           1281.75         1478.63          850.33           852.04   
35            415.50          633.78          349.61           358.68   
44    

In [209]:
#concatenate regions back together
frames = [central_valley_gas,sf_midcoast_gas,mountain_gas]
bas_gas_usage=pd.concat(frames,sort=True)
bas_gas_usage

15_HI_hh_count  15_LI_hh_count  15_MoI_hh_count  15_VLI_hh_count  \
5           2765.50         2051.20          1535.12          2939.20   
22         19249.99         5548.34          7023.62          5699.97   
23          1186.42          873.65           874.08          1304.12   
35           534.89          332.47           276.42           419.17   
44           576.58          424.58           424.79           633.78   
48           498.96          367.43           367.61           548.46   
50         60807.56        26071.65         26808.97         48959.44   
55           660.74          410.70           341.46           517.80   
63           432.43          318.44           318.59           475.33   
65          1064.45          783.84           784.22          1170.05   
67          1336.61          641.55           587.59          1045.59   
73          1048.80          651.90           542.00           821.90   
78          3597.38         2236.02          1859.06          2819.12   
83           698.54          514.39           514.65           767.84   
85          7780.65         5771.00          4319.02          8269.35   
102          734.40          352.50           322.85           574.50   
107         1145.66          549.90           503.65           896.22   
120         2247.26         1078.65           987.92          1757.97   
135          255.02          187.79           187.89           280.32   
144         2335.39         1120.95          1026.66          1826.91   
153         1862.78         1371.72          1372.39          2047.58   
169        19638.22        10348.43         10233.10         17231.95   
172         8404.22         5676.56          4487.54          7638.02   
0          11593.90         5555.39          6227.37          8029.06   
1           3056.84          927.50          1374.20          2018.25   
2           2319.08          906.44           918.76          1264.18   
3           9484.27         7078.68          7361.23          9037.90   
4           1036.48          310.21           243.75           683.05   
7           6138.72         1523.23          1089.50          2621.16   
8            504.88          105.55            95.47           265.58   
..              ...             ...              ...              ...   
187        15821.10         6785.02          8034.80         11866.62   
188        17601.11         3446.44          6207.32          4888.76   
190         5106.00         2198.34          1272.08          3881.11   
192          564.98          324.78           266.81           501.42   
193         3586.02         1408.85          1649.54          1624.45   
196          888.41          265.90           208.93           585.47   
197          489.35          191.27           193.87           266.75   
5           2765.50         2051.20          1535.12          2939.20   
22         19249.99         5548.34          7023.62          5699.97   
23          1186.42          873.65           874.08          1304.12   
35           534.89          332.47           276.42           419.17   
44           576.58          424.58           424.79           633.78   
48           498.96          367.43           367.61           548.46   
50         60807.56        26071.65         26808.97         48959.44   
55           660.74          410.70           341.46           517.80   
63           432.43          318.44           318.59           475.33   
65          1064.45          783.84           784.22          1170.05   
67          1336.61          641.55           587.59          1045.59   
73          1048.80          651.90           542.00           821.90   
78          3597.38         2236.02          1859.06          2819.12   
83           698.54          514.39           514.65           767.84   
85          7780.65         5771.00          4319.02          8269.35   
102          734.40          352.50           322.85           

In [210]:
#calculate total gas usage by year
bas_gas_usage["2015_gas_usage"]=(bas_gas_usage["15_VLI_hh_count"]+bas_gas_usage["15_HI_hh_count"]+bas_gas_usage["15_LI_hh_count"]+bas_gas_usage["15_MoI_hh_count"])*12
bas_gas_usage["2016_gas_usage"]=(bas_gas_usage["16_VLI_hh_count"]+bas_gas_usage["16_HI_hh_count"]+bas_gas_usage["16_LI_hh_count"]+bas_gas_usage["16_MoI_hh_count"])*12
bas_gas_usage["2017_gas_usage"]=(bas_gas_usage["17_VLI_hh_count"]+bas_gas_usage["17_HI_hh_count"]+bas_gas_usage["17_LI_hh_count"]+bas_gas_usage["17_MoI_hh_count"])*12
bas_gas_usage["2018_gas_usage"]=(bas_gas_usage["18_VLI_hh_count"]+bas_gas_usage["18_HI_hh_count"]+bas_gas_usage["18_LI_hh_count"]+bas_gas_usage["18_MoI_hh_count"])*12
bas_gas_usage

15_HI_hh_count  15_LI_hh_count  15_MoI_hh_count  15_VLI_hh_count  \
5           2765.50         2051.20          1535.12          2939.20   
22         19249.99         5548.34          7023.62          5699.97   
23          1186.42          873.65           874.08          1304.12   
35           534.89          332.47           276.42           419.17   
44           576.58          424.58           424.79           633.78   
48           498.96          367.43           367.61           548.46   
50         60807.56        26071.65         26808.97         48959.44   
55           660.74          410.70           341.46           517.80   
63           432.43          318.44           318.59           475.33   
65          1064.45          783.84           784.22          1170.05   
67          1336.61          641.55           587.59          1045.59   
73          1048.80          651.90           542.00           821.90   
78          3597.38         2236.02          1859.06          2819.12   
83           698.54          514.39           514.65           767.84   
85          7780.65         5771.00          4319.02          8269.35   
102          734.40          352.50           322.85           574.50   
107         1145.66          549.90           503.65           896.22   
120         2247.26         1078.65           987.92          1757.97   
135          255.02          187.79           187.89           280.32   
144         2335.39         1120.95          1026.66          1826.91   
153         1862.78         1371.72          1372.39          2047.58   
169        19638.22        10348.43         10233.10         17231.95   
172         8404.22         5676.56          4487.54          7638.02   
0          11593.90         5555.39          6227.37          8029.06   
1           3056.84          927.50          1374.20          2018.25   
2           2319.08          906.44           918.76          1264.18   
3           9484.27         7078.68          7361.23          9037.90   
4           1036.48          310.21           243.75           683.05   
7           6138.72         1523.23          1089.50          2621.16   
8            504.88          105.55            95.47           265.58   
..              ...             ...              ...              ...   
187        15821.10         6785.02          8034.80         11866.62   
188        17601.11         3446.44          6207.32          4888.76   
190         5106.00         2198.34          1272.08          3881.11   
192          564.98          324.78           266.81           501.42   
193         3586.02         1408.85          1649.54          1624.45   
196          888.41          265.90           208.93           585.47   
197          489.35          191.27           193.87           266.75   
5           2765.50         2051.20          1535.12          2939.20   
22         19249.99         5548.34          7023.62          5699.97   
23          1186.42          873.65           874.08          1304.12   
35           534.89          332.47           276.42           419.17   
44           576.58          424.58           424.79           633.78   
48           498.96          367.43           367.61           548.46   
50         60807.56        26071.65         26808.97         48959.44   
55           660.74          410.70           341.46           517.80   
63           432.43          318.44           318.59           475.33   
65          1064.45          783.84           784.22          1170.05   
67          1336.61          641.55           587.59          1045.59   
73          1048.80          651.90           542.00           821.90   
78          3597.38         2236.02          1859.06          2819.12   
83           698.54          514.39           514.65           767.84   
85          7780.65         5771.00          4319.02          8269.35   
102          734.40          352.50           322.85           

In [241]:
bas_gas_usage[bas_gas_usage["2015_gas_usage"].isna()]

Empty DataFrame
Columns: [15_HI_hh_count, 15_LI_hh_count, 15_MoI_hh_count, 15_VLI_hh_count, 16_HI_hh_count, 16_LI_hh_count, 16_MoI_hh_count, 16_VLI_hh_count, 17_HI_hh_count, 17_LI_hh_count, 17_MoI_hh_count, 17_VLI_hh_count, 18_HI_hh_count, 18_LI_hh_count, 18_MoI_hh_count, 18_VLI_hh_count, County_x, PUMA, Place, gas_usage, 2015_gas_usage, 2016_gas_usage, 2017_gas_usage, 2018_gas_usage, 2015_gas_ghg, 2016_gas_ghg, 2017_gas_ghg, 2018_gas_ghg]
Index: []

In [211]:
#calculate GHGs from gas usage
bas_gas_usage["2015_gas_ghg"]=bas_gas_usage["2015_gas_usage"]*0.00531
bas_gas_usage["2016_gas_ghg"]=bas_gas_usage["2016_gas_usage"]*0.00531
bas_gas_usage["2017_gas_ghg"]=bas_gas_usage["2017_gas_usage"]*0.00531
bas_gas_usage["2018_gas_ghg"]=bas_gas_usage["2018_gas_usage"]*0.00531
bas_gas_usage

15_HI_hh_count  15_LI_hh_count  15_MoI_hh_count  15_VLI_hh_count  \
5           2765.50         2051.20          1535.12          2939.20   
22         19249.99         5548.34          7023.62          5699.97   
23          1186.42          873.65           874.08          1304.12   
35           534.89          332.47           276.42           419.17   
44           576.58          424.58           424.79           633.78   
48           498.96          367.43           367.61           548.46   
50         60807.56        26071.65         26808.97         48959.44   
55           660.74          410.70           341.46           517.80   
63           432.43          318.44           318.59           475.33   
65          1064.45          783.84           784.22          1170.05   
67          1336.61          641.55           587.59          1045.59   
73          1048.80          651.90           542.00           821.90   
78          3597.38         2236.02          1859.06          2819.12   
83           698.54          514.39           514.65           767.84   
85          7780.65         5771.00          4319.02          8269.35   
102          734.40          352.50           322.85           574.50   
107         1145.66          549.90           503.65           896.22   
120         2247.26         1078.65           987.92          1757.97   
135          255.02          187.79           187.89           280.32   
144         2335.39         1120.95          1026.66          1826.91   
153         1862.78         1371.72          1372.39          2047.58   
169        19638.22        10348.43         10233.10         17231.95   
172         8404.22         5676.56          4487.54          7638.02   
0          11593.90         5555.39          6227.37          8029.06   
1           3056.84          927.50          1374.20          2018.25   
2           2319.08          906.44           918.76          1264.18   
3           9484.27         7078.68          7361.23          9037.90   
4           1036.48          310.21           243.75           683.05   
7           6138.72         1523.23          1089.50          2621.16   
8            504.88          105.55            95.47           265.58   
..              ...             ...              ...              ...   
187        15821.10         6785.02          8034.80         11866.62   
188        17601.11         3446.44          6207.32          4888.76   
190         5106.00         2198.34          1272.08          3881.11   
192          564.98          324.78           266.81           501.42   
193         3586.02         1408.85          1649.54          1624.45   
196          888.41          265.90           208.93           585.47   
197          489.35          191.27           193.87           266.75   
5           2765.50         2051.20          1535.12          2939.20   
22         19249.99         5548.34          7023.62          5699.97   
23          1186.42          873.65           874.08          1304.12   
35           534.89          332.47           276.42           419.17   
44           576.58          424.58           424.79           633.78   
48           498.96          367.43           367.61           548.46   
50         60807.56        26071.65         26808.97         48959.44   
55           660.74          410.70           341.46           517.80   
63           432.43          318.44           318.59           475.33   
65          1064.45          783.84           784.22          1170.05   
67          1336.61          641.55           587.59          1045.59   
73          1048.80          651.90           542.00           821.90   
78          3597.38         2236.02          1859.06          2819.12   
83           698.54          514.39           514.65           767.84   
85          7780.65         5771.00          4319.02          8269.35   
102          734.40          352.50           322.85           

## Part C2. Calculate Gas Usage for Needs Scenario

In [212]:
#calulate gas usage for BAS scenario
needs_gas = needs_df[["Place",
    "15_HI_hh_mod",
    "15_LI_hh_mod",
    "15_MoI_hh_mod",
    "15_VLI_hh_mod",
    "16_HI_hh_mod",
    "16_LI_hh_mod",
    "16_MoI_hh_mod",
    "16_VLI_hh_mod",
    "17_HI_hh_mod",
    "17_LI_hh_mod",
    "17_MoI_hh_mod",
    "17_VLI_hh_mod",
    "18_HI_hh_mod",
    "18_LI_hh_mod",
    "18_MoI_hh_mod",
    "18_VLI_hh_mod",
    "County_x"]].copy()
needs_gas

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
0              Alameda city, CA      13503.94       5555.39        7857.53   
1               Albany city, CA       3104.72        927.50        1374.20   
2      American Canyon city, CA       2403.45        906.44        1024.66   
3              Antioch city, CA      10636.05       7078.68        7670.68   
4             Atherton town, CA       1293.82        333.31         243.75   
5              Atwater city, CA       4068.25       2051.20        1535.12   
6               Auburn city, CA       2544.26        681.03         852.18   
7              Belmont city, CA       6054.70       1523.23        1152.31   
8            Belvedere city, CA        560.86        157.93         100.69   
9              Benicia city, CA       4829.00       1723.20        2216.60   
10            Berkeley city, CA      19457.62       5793.50        8583.80   
11           Brentwood city, CA       9385.28       2302.57        4761.68   
12            Brisbane city, CA        821.56        395.97         304.56   
13          Burlingame city, CA       6626.00       1905.39        1691.33   
14           Calistoga city, CA        926.10        349.27         392.53   
15            Campbell city, CA       7418.66       2797.12        3466.70   
16            Capitola city, CA        815.73        359.25          50.83   
17   Carmel-by-the-Sea city, CA       1742.16        481.71         450.62   
18               Ceres city, CA       6305.70       2133.04        2680.77   
19      Citrus Heights city, CA      11836.51       7814.18        6614.34   
20             Clayton city, CA       2423.82        453.27         979.97   
21          Cloverdale city, CA       1430.64        503.16         589.15   
22              Clovis city, CA      21794.80       5548.34        7023.62   
23            Coalinga city, CA       1266.02        873.65         874.08   
24              Colfax city, CA        387.70        103.78         129.86   
25               Colma town, CA        194.53        101.00         110.51   
26             Concord city, CA      22210.65       6438.88       11214.54   
27        Corte Madera town, CA       2173.35        612.14         389.87   
28              Cotati city, CA       1555.49        601.33         851.33   
29           Cupertino city, CA      12854.34       2715.59        3299.67   
..                          ...           ...           ...            ...   
168    Unincorporated_El Dorado      19956.44       3000.22        6386.34   
169       Unincorporated_Fresno      21269.52      10348.43       10233.10   
170        Unincorporated_Marin      14196.33       4726.67        3634.44   
171    Unincorporated_Mendocino       3834.85       2423.22        3498.81   
172       Unincorporated_Merced      10724.90       5676.56        4487.54   
173     Unincorporated_Monterey      22044.05       7372.59        6906.14   
174         Unincorporated_Napa       4983.30       1879.42        2113.48   
175       Unincorporated_Placer      23096.66       6116.82        7820.19   
176   Unincorporated_Sacramento      73278.77      31884.34       36533.96   
177  Unincorporated_San Joaquin      13665.12       7004.25        6871.86   
178    Unincorporated_San Mateo      11614.82       2989.60        2391.07   
179  Unincorporated_Santa Clara      13726.18       4357.16        5104.08   
180   Unincorporated_Santa Cruz      18047.76       6518.07        3039.31   
181       Unincorporated_Solano       3681.29       1185.21        1573.59   
182       Unincorporated_Sonoma      28479.06      10519.43       12464.20   
183   Unincorporated_Stanislaus      16279.40       5537.21        6709.14   
184         Unincorporated_Yolo        854.39        735.68         878.97   
185         Union City city, CA      13215.02       3124.74        5316.54   
186          Vacaville city, CA      16869.01       5115.73        6953.01   
187            Vallejo city, CA      19017.48   

In [213]:
sf_midcoast_mask = (needs_gas["County_x"]=="Alameda")|(needs_gas["County_x"]=="Alameda")|(needs_gas["County_x"]=="Contra Costa")|(needs_gas["County_x"]=="Lake")|(needs_gas["County_x"]=="Marin")|(needs_gas["County_x"]=="Mendocino")|(needs_gas["County_x"]=="Monterey")|(needs_gas["County_x"]=="Napa")|(needs_gas["County_x"]=="San Benito")|(needs_gas["County_x"]=="San Francisco")|(needs_gas["County_x"]=="San Mateo")|(needs_gas["County_x"]=="Santa Clara")|(needs_gas["County_x"]=="Santa Cruz")|(needs_gas["County_x"]=="Solano")|(needs_gas["County_x"]=="Sonoma")
sf_midcoast_gas = needs_gas[sf_midcoast_mask].copy()
sf_midcoast_gas["gas_usage"]=35.5
sf_midcoast_gas

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
0                Alameda city, CA      13503.94       5555.39        7857.53   
1                 Albany city, CA       3104.72        927.50        1374.20   
2        American Canyon city, CA       2403.45        906.44        1024.66   
3                Antioch city, CA      10636.05       7078.68        7670.68   
4               Atherton town, CA       1293.82        333.31         243.75   
7                Belmont city, CA       6054.70       1523.23        1152.31   
8              Belvedere city, CA        560.86        157.93         100.69   
9                Benicia city, CA       4829.00       1723.20        2216.60   
10              Berkeley city, CA      19457.62       5793.50        8583.80   
11             Brentwood city, CA       9385.28       2302.57        4761.68   
12              Brisbane city, CA        821.56        395.97         304.56   
13            Burlingame city, CA       6626.00       1905.39        1691.33   
14             Calistoga city, CA        926.10        349.27         392.53   
15              Campbell city, CA       7418.66       2797.12        3466.70   
16              Capitola city, CA        815.73        359.25          50.83   
17     Carmel-by-the-Sea city, CA       1742.16        481.71         450.62   
20               Clayton city, CA       2423.82        453.27         979.97   
21            Cloverdale city, CA       1430.64        503.16         589.15   
25                 Colma town, CA        194.53        101.00         110.51   
26               Concord city, CA      22210.65       6438.88       11214.54   
27          Corte Madera town, CA       2173.35        612.14         389.87   
28                Cotati city, CA       1555.49        601.33         851.33   
29             Cupertino city, CA      12854.34       2715.59        3299.67   
30             Daly City city, CA      10990.19       5886.34        6185.63   
31              Danville town, CA      10735.67       1179.38        2701.20   
33          Del Rey Oaks city, CA        378.73        104.72          97.96   
34                 Dixon city, CA       3164.46        959.66        1304.01   
36                Dublin city, CA      11166.95       1317.78        3589.78   
37        East Palo Alto city, CA       4153.55       1033.59         758.32   
38            El Cerrito city, CA       4292.60       1194.04        2712.59   
..                            ...           ...           ...            ...   
151              Seaside city, CA       5567.33       1539.38        1440.01   
152           Sebastopol city, CA       1466.41        515.74         603.85   
154              Soledad city, CA       1737.14        757.77         718.50   
155               Sonoma city, CA       2324.79        817.63         957.32   
157  South San Francisco city, CA       9358.64       4510.59        3487.05   
158           St. Helena city, CA       1124.55        424.12         476.66   
160          Suisun City city, CA       4490.53       1670.40        2033.81   
161            Sunnyvale city, CA      31545.36       6753.77       10480.75   
162              Tiburon town, CA       2173.35        612.51         390.62   
165                Ukiah city, CA        792.23        500.60         722.81   
166        Unincorporated_Alameda      19227.72       8670.08       13528.85   
167   Unincorporated_Contra Costa      29979.88       7417.54       14484.63   
170          Unincorporated_Marin      14196.33       4726.67        3634.44   
171      Unincorporated_Mendocino       3834.85       2423.22        3498.81   
173       Unincorporated_Monterey      22044.05       7372.59        6906.14   
174           Unincorporated_Napa       4983.30       1879.42        2113.48   
178      Unincorporated_San Mateo      11614.82       2989.60        2391.07   
179    Unincorporated_Santa Clara      13726.18       4357.16        5104.08   
180     Unincorporated_Santa

In [214]:
central_valley_mask = (needs_gas["County_x"]=="Fresno")|(needs_gas["County_x"]=="Kern")|(needs_gas["County_x"]=="Kings")|(needs_gas["County_x"]=="Madera")|(needs_gas["County_x"]=="Mariposa")|(needs_gas["County_x"]=="Merced")|(needs_gas["County_x"]=="Tulare")|(needs_gas["County_x"]=="Tuolumne")
central_valley_gas = needs_gas[central_valley_mask].copy()
central_valley_gas["gas_usage"]=33.5
central_valley_gas

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
5         Atwater city, CA       4068.25       2051.20        1535.12   
22         Clovis city, CA      21794.80       5548.34        7023.62   
23       Coalinga city, CA       1266.02        873.65         874.08   
35      Dos Palos city, CA        597.82        332.47         276.42   
44      Firebaugh city, CA        615.26        424.58         424.79   
48         Fowler city, CA        532.44        367.43         367.61   
50         Fresno city, CA      69420.50      26071.65       26808.97   
55        Gustine city, CA        738.49        410.70         341.46   
63          Huron city, CA        461.45        318.44         318.59   
65         Kerman city, CA       1135.87        783.84         784.22   
67      Kingsburg city, CA       1343.43        641.55         587.59   
73     Livingston city, CA       1172.20        651.90         542.00   
78      Los Banos city, CA       4020.65       2236.02        1859.06   
83        Mendota city, CA        745.42        514.39         514.65   
85         Merced city, CA      11445.90       5771.00        4319.02   
102   Orange Cove city, CA        738.15        352.50         322.85   
107       Parlier city, CA       1151.51        549.90         503.65   
120       Reedley city, CA       2258.74       1078.65         987.92   
135   San Joaquin city, CA        272.14        187.79         187.89   
144        Sanger city, CA       2347.32       1120.95        1026.66   
153         Selma city, CA       1987.78       1371.72        1372.39   
169  Unincorporated_Fresno      21269.52      10348.43       10233.10   
172  Unincorporated_Merced      10724.90       5676.56        4487.54   

     15_VLI_hh_mod  16_HI_hh_mod  16_LI_hh_mod  16_MoI_hh_mod  16_VLI_hh_mod  \
5          2939.20       3160.38       1683.73        1706.70        2333.56   
22         5699.97      19693.03       4875.43        5724.26        5786.72   
23         1304.12       1182.56       1020.67         622.85        1281.75   
35          419.17        525.10        400.86         254.59         415.50   
44          633.78        574.70        496.03         302.69         622.91   
48          548.46        497.34        429.25         261.94         539.05   
50        48959.44      62744.18      23858.15       25931.87       52159.06   
55          517.80        648.65        495.18         314.50         513.26   
63          475.33        431.03        372.02         227.02         467.18   
65         1170.05       1060.99        915.74         558.82        1149.98   
67         1045.59       1649.28        594.96         454.55         881.61   
73          821.90       1029.60        786.00         499.20         814.70   
78         2819.12       3531.53       2695.98        1712.26        2794.42   
83          767.84        696.28        600.96         366.72         754.68   
85         8269.35       8891.62       4737.13        4801.75        6565.41   
102         574.50        906.20        326.90         249.75         484.40   
107         896.22       1413.67        509.96         389.61         755.66   
120        1757.97       2772.97       1000.31         764.24        1482.26   
135         280.32        254.20        219.40         133.88         275.52   
144        1826.91       2881.72       1039.54         794.21        1540.39   
153        2047.58       1856.74       1602.55         977.93        2012.47   
169       17231.95      21517.71      10374.43        8278.38       16714.47   
172        7638.02       8857.46       5768.53        4532.17        6780.91   

     17_HI_hh_mod  17_LI_hh_mod  17_MoI_hh_mod  17_VLI_hh_mod  18_HI_hh_mod  \
5         3276.56       1555.58        1530.10        2839.80       4068.25   
22       20584.44       4555.65        5210.05        5141.71      21794.80   
23        1478.63        850.33         852.04        1174.43       1266.02   
35         633.78        349.61

In [215]:
mountain_mask = (needs_gas["County_x"]=="Alpine")|(needs_gas["County_x"]=="Amador")|(needs_gas["County_x"]=="Butte")|(needs_gas["County_x"]=="Calaveras")|(needs_gas["County_x"]=="Colusa")|(needs_gas["County_x"]=="Del Norte")|(needs_gas["County_x"]=="El Dorado")|(needs_gas["County_x"]=="Glenn")|(needs_gas["County_x"]=="Humboldt")|(needs_gas["County_x"]=="Placer")|(needs_gas["County_x"]=="Sacramento")|(needs_gas["County_x"]=="San Joaquin")|(needs_gas["County_x"]=="Stanislaus")|(needs_gas["County_x"]=="Yolo")|(needs_gas["County_x"]=="Yuba")
mountain_gas = needs_gas[central_valley_mask].copy()
mountain_gas["gas_usage"]=36.5
mountain_gas

Place  15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  \
5         Atwater city, CA       4068.25       2051.20        1535.12   
22         Clovis city, CA      21794.80       5548.34        7023.62   
23       Coalinga city, CA       1266.02        873.65         874.08   
35      Dos Palos city, CA        597.82        332.47         276.42   
44      Firebaugh city, CA        615.26        424.58         424.79   
48         Fowler city, CA        532.44        367.43         367.61   
50         Fresno city, CA      69420.50      26071.65       26808.97   
55        Gustine city, CA        738.49        410.70         341.46   
63          Huron city, CA        461.45        318.44         318.59   
65         Kerman city, CA       1135.87        783.84         784.22   
67      Kingsburg city, CA       1343.43        641.55         587.59   
73     Livingston city, CA       1172.20        651.90         542.00   
78      Los Banos city, CA       4020.65       2236.02        1859.06   
83        Mendota city, CA        745.42        514.39         514.65   
85         Merced city, CA      11445.90       5771.00        4319.02   
102   Orange Cove city, CA        738.15        352.50         322.85   
107       Parlier city, CA       1151.51        549.90         503.65   
120       Reedley city, CA       2258.74       1078.65         987.92   
135   San Joaquin city, CA        272.14        187.79         187.89   
144        Sanger city, CA       2347.32       1120.95        1026.66   
153         Selma city, CA       1987.78       1371.72        1372.39   
169  Unincorporated_Fresno      21269.52      10348.43       10233.10   
172  Unincorporated_Merced      10724.90       5676.56        4487.54   

     15_VLI_hh_mod  16_HI_hh_mod  16_LI_hh_mod  16_MoI_hh_mod  16_VLI_hh_mod  \
5          2939.20       3160.38       1683.73        1706.70        2333.56   
22         5699.97      19693.03       4875.43        5724.26        5786.72   
23         1304.12       1182.56       1020.67         622.85        1281.75   
35          419.17        525.10        400.86         254.59         415.50   
44          633.78        574.70        496.03         302.69         622.91   
48          548.46        497.34        429.25         261.94         539.05   
50        48959.44      62744.18      23858.15       25931.87       52159.06   
55          517.80        648.65        495.18         314.50         513.26   
63          475.33        431.03        372.02         227.02         467.18   
65         1170.05       1060.99        915.74         558.82        1149.98   
67         1045.59       1649.28        594.96         454.55         881.61   
73          821.90       1029.60        786.00         499.20         814.70   
78         2819.12       3531.53       2695.98        1712.26        2794.42   
83          767.84        696.28        600.96         366.72         754.68   
85         8269.35       8891.62       4737.13        4801.75        6565.41   
102         574.50        906.20        326.90         249.75         484.40   
107         896.22       1413.67        509.96         389.61         755.66   
120        1757.97       2772.97       1000.31         764.24        1482.26   
135         280.32        254.20        219.40         133.88         275.52   
144        1826.91       2881.72       1039.54         794.21        1540.39   
153        2047.58       1856.74       1602.55         977.93        2012.47   
169       17231.95      21517.71      10374.43        8278.38       16714.47   
172        7638.02       8857.46       5768.53        4532.17        6780.91   

     17_HI_hh_mod  17_LI_hh_mod  17_MoI_hh_mod  17_VLI_hh_mod  18_HI_hh_mod  \
5         3276.56       1555.58        1530.10        2839.80       4068.25   
22       20584.44       4555.65        5210.05        5141.71      21794.80   
23        1478.63        850.33         852.04        1174.43       1266.02   
35         633.78        349.61

In [216]:
#concatenate regions back together
frames = [central_valley_gas,sf_midcoast_gas,mountain_gas]
needs_gas_usage=pd.concat(frames,sort=True)
needs_gas_usage

15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  15_VLI_hh_mod  16_HI_hh_mod  \
5         4068.25       2051.20        1535.12        2939.20       3160.38   
22       21794.80       5548.34        7023.62        5699.97      19693.03   
23        1266.02        873.65         874.08        1304.12       1182.56   
35         597.82        332.47         276.42         419.17        525.10   
44         615.26        424.58         424.79         633.78        574.70   
48         532.44        367.43         367.61         548.46        497.34   
50       69420.50      26071.65       26808.97       48959.44      62744.18   
55         738.49        410.70         341.46         517.80        648.65   
63         461.45        318.44         318.59         475.33        431.03   
65        1135.87        783.84         784.22        1170.05       1060.99   
67        1343.43        641.55         587.59        1045.59       1649.28   
73        1172.20        651.90         542.00         821.90       1029.60   
78        4020.65       2236.02        1859.06        2819.12       3531.53   
83         745.42        514.39         514.65         767.84        696.28   
85       11445.90       5771.00        4319.02        8269.35       8891.62   
102        738.15        352.50         322.85         574.50        906.20   
107       1151.51        549.90         503.65         896.22       1413.67   
120       2258.74       1078.65         987.92        1757.97       2772.97   
135        272.14        187.79         187.89         280.32        254.20   
144       2347.32       1120.95        1026.66        1826.91       2881.72   
153       1987.78       1371.72        1372.39        2047.58       1856.74   
169      21269.52      10348.43       10233.10       17231.95      21517.71   
172      10724.90       5676.56        4487.54        7638.02       8857.46   
0        13503.94       5555.39        7857.53        8260.24      13287.26   
1         3104.72        927.50        1374.20        2170.94       3501.06   
2         2403.45        906.44        1024.66        1465.40       2435.50   
3        10636.05       7078.68        7670.68       11700.43      10886.61   
4         1293.82        333.31         243.75         683.05       1293.07   
7         6054.70       1523.23        1152.31        2801.12       5836.54   
8          560.86        157.93         100.69         265.58        518.13   
..            ...           ...            ...            ...           ...   
187      19017.48       6785.02        8726.71       12172.47      15399.34   
188      19467.21       3446.44        6969.63        5085.21      18664.67   
190       6465.85       2198.34        1272.08        3881.11       5320.73   
192        248.72        157.17         226.93         501.42        482.39   
193       4005.79       1408.85        1649.54        1880.25       3890.88   
196       1113.20        284.53         208.93         585.47       1110.45   
197        507.15        191.27         193.87         266.75        513.91   
5         4068.25       2051.20        1535.12        2939.20       3160.38   
22       21794.80       5548.34        7023.62        5699.97      19693.03   
23        1266.02        873.65         874.08        1304.12       1182.56   
35         597.82        332.47         276.42         419.17        525.10   
44         615.26        424.58         424.79         633.78        574.70   
48         532.44        367.43         367.61         548.46        497.34   
50       69420.50      26071.65       26808.97       48959.44      62744.18   
55         738.49        410.70         341.46         517.80        648.65   
63         461.45        318.44         318.59         475.33        431.03   
65        1135.87        783.84         784.22        1170.05       1060.99   
67        1343.43        641.55         587.59        1045.59       1649.28   
73        1172.20        651.90         542.00         

In [217]:
#calculate total gas usage by year
needs_gas_usage["2015_gas_usage"]=(needs_gas_usage["15_VLI_hh_mod"]+needs_gas_usage["15_HI_hh_mod"]+needs_gas_usage["15_LI_hh_mod"]+needs_gas_usage["15_MoI_hh_mod"])*12
needs_gas_usage["2016_gas_usage"]=(needs_gas_usage["16_VLI_hh_mod"]+needs_gas_usage["16_HI_hh_mod"]+needs_gas_usage["16_LI_hh_mod"]+needs_gas_usage["16_MoI_hh_mod"])*12
needs_gas_usage["2017_gas_usage"]=(needs_gas_usage["17_VLI_hh_mod"]+needs_gas_usage["17_HI_hh_mod"]+needs_gas_usage["17_LI_hh_mod"]+needs_gas_usage["17_MoI_hh_mod"])*12
needs_gas_usage["2018_gas_usage"]=(needs_gas_usage["18_VLI_hh_mod"]+needs_gas_usage["18_HI_hh_mod"]+needs_gas_usage["18_LI_hh_mod"]+needs_gas_usage["18_MoI_hh_mod"])*12
needs_gas_usage

15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  15_VLI_hh_mod  16_HI_hh_mod  \
5         4068.25       2051.20        1535.12        2939.20       3160.38   
22       21794.80       5548.34        7023.62        5699.97      19693.03   
23        1266.02        873.65         874.08        1304.12       1182.56   
35         597.82        332.47         276.42         419.17        525.10   
44         615.26        424.58         424.79         633.78        574.70   
48         532.44        367.43         367.61         548.46        497.34   
50       69420.50      26071.65       26808.97       48959.44      62744.18   
55         738.49        410.70         341.46         517.80        648.65   
63         461.45        318.44         318.59         475.33        431.03   
65        1135.87        783.84         784.22        1170.05       1060.99   
67        1343.43        641.55         587.59        1045.59       1649.28   
73        1172.20        651.90         542.00         821.90       1029.60   
78        4020.65       2236.02        1859.06        2819.12       3531.53   
83         745.42        514.39         514.65         767.84        696.28   
85       11445.90       5771.00        4319.02        8269.35       8891.62   
102        738.15        352.50         322.85         574.50        906.20   
107       1151.51        549.90         503.65         896.22       1413.67   
120       2258.74       1078.65         987.92        1757.97       2772.97   
135        272.14        187.79         187.89         280.32        254.20   
144       2347.32       1120.95        1026.66        1826.91       2881.72   
153       1987.78       1371.72        1372.39        2047.58       1856.74   
169      21269.52      10348.43       10233.10       17231.95      21517.71   
172      10724.90       5676.56        4487.54        7638.02       8857.46   
0        13503.94       5555.39        7857.53        8260.24      13287.26   
1         3104.72        927.50        1374.20        2170.94       3501.06   
2         2403.45        906.44        1024.66        1465.40       2435.50   
3        10636.05       7078.68        7670.68       11700.43      10886.61   
4         1293.82        333.31         243.75         683.05       1293.07   
7         6054.70       1523.23        1152.31        2801.12       5836.54   
8          560.86        157.93         100.69         265.58        518.13   
..            ...           ...            ...            ...           ...   
187      19017.48       6785.02        8726.71       12172.47      15399.34   
188      19467.21       3446.44        6969.63        5085.21      18664.67   
190       6465.85       2198.34        1272.08        3881.11       5320.73   
192        248.72        157.17         226.93         501.42        482.39   
193       4005.79       1408.85        1649.54        1880.25       3890.88   
196       1113.20        284.53         208.93         585.47       1110.45   
197        507.15        191.27         193.87         266.75        513.91   
5         4068.25       2051.20        1535.12        2939.20       3160.38   
22       21794.80       5548.34        7023.62        5699.97      19693.03   
23        1266.02        873.65         874.08        1304.12       1182.56   
35         597.82        332.47         276.42         419.17        525.10   
44         615.26        424.58         424.79         633.78        574.70   
48         532.44        367.43         367.61         548.46        497.34   
50       69420.50      26071.65       26808.97       48959.44      62744.18   
55         738.49        410.70         341.46         517.80        648.65   
63         461.45        318.44         318.59         475.33        431.03   
65        1135.87        783.84         784.22        1170.05       1060.99   
67        1343.43        641.55         587.59        1045.59       1649.28   
73        1172.20        651.90         542.00         

In [218]:
#calculate GHGs from gas usage
needs_gas_usage["2015_gas_ghg"]=needs_gas_usage["2015_gas_usage"]*0.00531
needs_gas_usage["2016_gas_ghg"]=needs_gas_usage["2016_gas_usage"]*0.00531
needs_gas_usage["2017_gas_ghg"]=needs_gas_usage["2017_gas_usage"]*0.00531
needs_gas_usage["2018_gas_ghg"]=needs_gas_usage["2018_gas_usage"]*0.00531
needs_gas_usage

15_HI_hh_mod  15_LI_hh_mod  15_MoI_hh_mod  15_VLI_hh_mod  16_HI_hh_mod  \
5         4068.25       2051.20        1535.12        2939.20       3160.38   
22       21794.80       5548.34        7023.62        5699.97      19693.03   
23        1266.02        873.65         874.08        1304.12       1182.56   
35         597.82        332.47         276.42         419.17        525.10   
44         615.26        424.58         424.79         633.78        574.70   
48         532.44        367.43         367.61         548.46        497.34   
50       69420.50      26071.65       26808.97       48959.44      62744.18   
55         738.49        410.70         341.46         517.80        648.65   
63         461.45        318.44         318.59         475.33        431.03   
65        1135.87        783.84         784.22        1170.05       1060.99   
67        1343.43        641.55         587.59        1045.59       1649.28   
73        1172.20        651.90         542.00         821.90       1029.60   
78        4020.65       2236.02        1859.06        2819.12       3531.53   
83         745.42        514.39         514.65         767.84        696.28   
85       11445.90       5771.00        4319.02        8269.35       8891.62   
102        738.15        352.50         322.85         574.50        906.20   
107       1151.51        549.90         503.65         896.22       1413.67   
120       2258.74       1078.65         987.92        1757.97       2772.97   
135        272.14        187.79         187.89         280.32        254.20   
144       2347.32       1120.95        1026.66        1826.91       2881.72   
153       1987.78       1371.72        1372.39        2047.58       1856.74   
169      21269.52      10348.43       10233.10       17231.95      21517.71   
172      10724.90       5676.56        4487.54        7638.02       8857.46   
0        13503.94       5555.39        7857.53        8260.24      13287.26   
1         3104.72        927.50        1374.20        2170.94       3501.06   
2         2403.45        906.44        1024.66        1465.40       2435.50   
3        10636.05       7078.68        7670.68       11700.43      10886.61   
4         1293.82        333.31         243.75         683.05       1293.07   
7         6054.70       1523.23        1152.31        2801.12       5836.54   
8          560.86        157.93         100.69         265.58        518.13   
..            ...           ...            ...            ...           ...   
187      19017.48       6785.02        8726.71       12172.47      15399.34   
188      19467.21       3446.44        6969.63        5085.21      18664.67   
190       6465.85       2198.34        1272.08        3881.11       5320.73   
192        248.72        157.17         226.93         501.42        482.39   
193       4005.79       1408.85        1649.54        1880.25       3890.88   
196       1113.20        284.53         208.93         585.47       1110.45   
197        507.15        191.27         193.87         266.75        513.91   
5         4068.25       2051.20        1535.12        2939.20       3160.38   
22       21794.80       5548.34        7023.62        5699.97      19693.03   
23        1266.02        873.65         874.08        1304.12       1182.56   
35         597.82        332.47         276.42         419.17        525.10   
44         615.26        424.58         424.79         633.78        574.70   
48         532.44        367.43         367.61         548.46        497.34   
50       69420.50      26071.65       26808.97       48959.44      62744.18   
55         738.49        410.70         341.46         517.80        648.65   
63         461.45        318.44         318.59         475.33        431.03   
65        1135.87        783.84         784.22        1170.05       1060.99   
67        1343.43        641.55         587.59        1045.59       1649.28   
73        1172.20        651.90         542.00         

## Part D. Create Table with all GHG emissions

In [231]:
#filter vmt df for sums variables
bas_ghg = bas_df[["Place","County_x","15_total_VMT","16_total_VMT","17_total_VMT","18_total_VMT","15_vmt_ghg","16_vmt_ghg","17_vmt_ghg","18_vmt_ghg"]].copy()
bas_ghg

Place      County_x  15_total_VMT  16_total_VMT  \
0              Alameda city, CA       Alameda  299300335.21  313705909.55   
1               Albany city, CA       Alameda   73717952.11   75010265.94   
2      American Canyon city, CA          Napa   68201984.88   68314746.91   
3              Antioch city, CA  Contra Costa  430142952.65  447422463.77   
4             Atherton town, CA     San Mateo   25654082.02   26734981.81   
5              Atwater city, CA        Merced  102866439.59  101584731.21   
6               Auburn city, CA        Placer   60838999.75   60112943.70   
7              Belmont city, CA     San Mateo  128138419.69  123568682.94   
8            Belvedere city, CA         Marin    9128503.41    9390400.53   
9              Benicia city, CA        Solano  117605456.02  113264826.18   
10            Berkeley city, CA       Alameda  426069848.79  433634021.57   
11           Brentwood city, CA  Contra Costa  234550508.21  243340685.04   
12            Brisbane city, CA     San Mateo   18239122.54   17771619.19   
13          Burlingame city, CA     San Mateo  127751793.01  135867520.48   
14           Calistoga city, CA          Napa   23320337.16   23375980.56   
15            Campbell city, CA   Santa Clara  197160033.19  194569648.97   
16            Capitola city, CA    Santa Cruz   48901213.28   50805498.21   
17   Carmel-by-the-Sea city, CA      Monterey   34521352.20   34900751.62   
18               Ceres city, CA    Stanislaus  119094076.51  124625298.56   
19      Citrus Heights city, CA    Sacramento  366634028.97  377529031.58   
20             Clayton city, CA  Contra Costa   55904004.52   53979229.03   
21          Cloverdale city, CA        Sonoma   41158765.83   41106644.15   
22              Clovis city, CA        Fresno  455069511.10  439886335.12   
23            Coalinga city, CA        Fresno   59272604.68   57166676.21   
24              Colfax city, CA        Placer    9109021.05    8995976.08   
25               Colma town, CA     San Mateo    5612143.78    5616996.75   
26             Concord city, CA  Contra Costa  559808822.15  547371076.92   
27        Corte Madera town, CA         Marin   36653744.87   37699054.74   
28              Cotati city, CA        Sonoma   36267330.62   34252149.48   
29           Cupertino city, CA   Santa Clara  254026933.77  246540833.29   
..                          ...           ...           ...           ...   
168    Unincorporated_El Dorado     El Dorado  787540617.52  805224620.88   
169       Unincorporated_Fresno        Fresno  780513324.85  774699404.13   
170        Unincorporated_Marin         Marin  277664312.89  277592785.05   
171    Unincorporated_Mendocino     Mendocino  282216179.33  278886442.01   
172       Unincorporated_Merced        Merced  414235011.36  412657629.12   
173     Unincorporated_Monterey      Monterey  544923456.42  547461520.11   
174         Unincorporated_Napa          Napa  155415813.03  155052840.57   
175       Unincorporated_Placer        Placer  562283474.59  555937715.30   
176   Unincorporated_Sacramento    Sacramento 2423182694.72 2423963045.88   
177  Unincorporated_San Joaquin   San Joaquin  639393785.34  645455015.91   
178    Unincorporated_San Mateo     San Mateo  240790266.87  245447229.86   
179  Unincorporated_Santa Clara   Santa Clara  397618496.42  396650725.31   
180   Unincorporated_Santa Cruz    Santa Cruz  644101475.50  667970439.44   
181       Unincorporated_Solano        Solano   87885672.22   92308825.74   
182       Unincorporated_Sonoma        Sonoma  764017035.92  757896242.00   
183   Unincorporated_Stanislaus    Stanislaus  416647222.13  420046986.94   
184         Unincorporated_Yolo          Yolo  109860970.63  108694789.95   
185         Union City city, CA       Alameda  260208424.87  269029169.49   
186          Vacaville city, CA        Solano  381443416.75  406247346.50   
187            Vallejo city, CA        Solano  492079646.79  474116196.31   
188       Walnut Creek

In [232]:
bas_gas_ghg = bas_gas_usage[["Place","2015_gas_usage","2016_gas_usage","2017_gas_usage","2018_gas_usage","2015_gas_ghg","2016_gas_ghg","2017_gas_ghg","2018_gas_ghg"]].copy()
bas_gas_ghg

Place  2015_gas_usage  2016_gas_usage  2017_gas_usage  \
5            Atwater city, CA       111492.24       106612.43       110424.56   
22            Clovis city, CA       450263.00       432953.34       425902.22   
23          Coalinga city, CA        50859.24        49294.04        52265.22   
35         Dos Palos city, CA        18755.35        19152.54        20085.23   
44         Firebaugh city, CA        24716.64        23955.98        25399.92   
48            Fowler city, CA        21389.40        20731.14        21980.70   
50            Fresno city, CA      1951771.52      1976319.16      1987763.39   
55           Gustine city, CA        23168.38        23659.02        24811.16   
63             Huron city, CA        18537.48        17966.99        19049.94   
65            Kerman city, CA        45630.72        44226.43        46892.16   
67         Kingsburg city, CA        43336.02        42964.74        41525.48   
73        Livingston city, CA        36775.20        37554.00        39382.80   
78         Los Banos city, CA       126138.94       128810.22       135083.00   
83           Mendota city, CA        29945.16        29023.60        30772.98   
85            Merced city, CA       313680.24       299951.03       310676.36   
102      Orange Cove city, CA        23811.00        23607.00        22816.20   
107          Parlier city, CA        37145.16        36826.92        35593.27   
120          Reedley city, CA        72861.66        72237.42        69817.57   
135      San Joaquin city, CA        10932.36        10595.92        11234.58   
144           Sanger city, CA        75718.98        75070.26        72555.52   
153            Selma city, CA        79853.76        77396.26        82061.28   
169     Unincorporated_Fresno       689420.40       682619.84       686714.50   
172     Unincorporated_Merced       314476.22       311268.83       324546.90   
0            Alameda city, CA       376868.74       389248.32       383439.17   
1             Albany city, CA        88521.48        89359.42        86371.99   
2    American Canyon city, CA        64901.65        64518.41        62500.16   
3            Antioch city, CA       395544.97       405017.34       410374.54   
4           Atherton town, CA        27281.77        28414.26        29613.28   
7            Belmont city, CA       136471.39       130787.14       134574.05   
8          Belvedere city, CA        11657.86        11971.20        11664.38   
..                        ...             ...             ...             ...   
187          Vallejo city, CA       510090.48       487934.21       497796.82   
188     Walnut Creek city, CA       385723.67       388477.85       378827.99   
190      Watsonville city, CA       149490.43       156227.04       157002.05   
192          Willits city, CA        19895.87        19450.37        19360.30   
193          Windsor town, CA        99226.18        97972.22       100027.20   
196         Woodside town, CA        23384.38        24355.08        25382.81   
197       Yountville city, CA        13694.84        13613.98        13188.11   
5            Atwater city, CA       111492.24       106612.43       110424.56   
22            Clovis city, CA       450263.00       432953.34       425902.22   
23          Coalinga city, CA        50859.24        49294.04        52265.22   
35         Dos Palos city, CA        18755.35        19152.54        20085.23   
44         Firebaugh city, CA        24716.64        23955.98        25399.92   
48            Fowler city, CA        21389.40        20731.14        21980.70   
50            Fresno city, CA      1951771.52      1976319.16      1987763.39   
55           Gustine city, CA        23168.38        23659.02        24811.16   
63             Huron city, CA        18537.48        17966.99        19049.94   
65            Kerman city, CA        45630.72        44226.43        46892.16   
67         Kingsburg city, CA        43336.02        42

In [233]:
bas_electric_ghg = bas_electric[["Place","15_electric_usage","16_electric_usage","17_electric_usage","18_electric_usage","15_electric_ghg","16_electric_ghg","17_electric_ghg","18_electric_ghg"]].copy()
bas_electric_ghg

Place  15_electric_usage  16_electric_usage  \
0              Alameda city, CA        13205480.51        13639261.13   
1               Albany city, CA         3101792.66         3131153.94   
2      American Canyon city, CA         3472373.59         3451869.24   
3              Antioch city, CA        23530640.76        24094144.04   
4             Atherton town, CA          955953.29          995635.67   
5              Atwater city, CA         6632580.45         6342284.50   
6               Auburn city, CA         3787921.70         3688936.44   
7              Belmont city, CA         4781957.58         4582781.25   
8            Belvedere city, CA          408491.27          419470.85   
9              Benicia city, CA         7716220.83         7370422.20   
10            Berkeley city, CA        19374965.74        19558367.34   
11           Brentwood city, CA        12344225.76        12983157.26   
12            Brisbane city, CA          781362.01          753141.91   
13          Burlingame city, CA         5067296.57         5347206.32   
14           Calistoga city, CA         1337978.82         1330078.06   
15            Campbell city, CA         8878478.47         8711059.80   
16            Capitola city, CA         2094094.68         2128160.29   
17   Carmel-by-the-Sea city, CA         1221742.48         1234682.33   
18               Ceres city, CA         9215621.96         9778027.30   
19      Citrus Heights city, CA        24144366.22        23995158.83   
20             Clayton city, CA         2984350.67         2880321.96   
21          Cloverdale city, CA         1896002.55         1872042.18   
22              Clovis city, CA        28789253.65        27682495.37   
23            Coalinga city, CA         3251876.23         3151799.56   
24              Colfax city, CA          577207.12          562123.65   
25               Colma town, CA          235465.44          234698.48   
26             Concord city, CA        33835631.91        32872818.31   
27        Corte Madera town, CA         1582903.69         1625449.54   
28              Cotati city, CA         2059359.39         1936518.18   
29           Cupertino city, CA        10841004.30        10564162.86   
..                          ...                ...                ...   
168    Unincorporated_El Dorado        24758845.00        25492736.83   
169       Unincorporated_Fresno        44080678.60        43645859.55   
170        Unincorporated_Marin        11821537.45        11829410.09   
171    Unincorporated_Mendocino        16412188.32        16044693.42   
172       Unincorporated_Merced        18707928.50        18517123.19   
173     Unincorporated_Monterey        21837337.08        21980153.98   
174         Unincorporated_Napa         7199600.30         7157086.68   
175       Unincorporated_Placer        20524622.43        20133315.87   
176   Unincorporated_Sacramento       149212802.58       149235942.67   
177  Unincorporated_San Joaquin        32619408.02        32513077.80   
178    Unincorporated_San Mateo         8885929.84         9048252.36   
179  Unincorporated_Santa Clara        15687804.51        15713575.87   
180   Unincorporated_Santa Cruz        21304831.44        21983690.94   
181       Unincorporated_Solano         5073733.22         5293842.19   
182       Unincorporated_Sonoma        38741706.87        38202569.59   
183   Unincorporated_Stanislaus        25352198.57        25509029.39   
184         Unincorporated_Yolo         5895366.90         5841078.51   
185         Union City city, CA         8814554.62         9133847.79   
186          Vacaville city, CA        22186345.03        23357822.83   
187            Vallejo city, CA        17873570.42        17097214.65   
188       Walnut Creek city, CA        22946379.57        23110223.45   
189          Waterford city, CA         1876563.63         1813267.64   
190        Watsonville city, CA         5238144.74         5474195.48   
191    West

In [234]:
bas_ghg = bas_ghg.merge(bas_gas_ghg,how="left",on="Place")
bas_ghg = bas_ghg.merge(bas_electric_ghg,how="left",on="Place")
bas_ghg

Place      County_x  15_total_VMT  16_total_VMT  \
0              Alameda city, CA       Alameda  299300335.21  313705909.55   
1               Albany city, CA       Alameda   73717952.11   75010265.94   
2      American Canyon city, CA          Napa   68201984.88   68314746.91   
3              Antioch city, CA  Contra Costa  430142952.65  447422463.77   
4             Atherton town, CA     San Mateo   25654082.02   26734981.81   
5              Atwater city, CA        Merced  102866439.59  101584731.21   
6              Atwater city, CA        Merced  102866439.59  101584731.21   
7               Auburn city, CA        Placer   60838999.75   60112943.70   
8              Belmont city, CA     San Mateo  128138419.69  123568682.94   
9            Belvedere city, CA         Marin    9128503.41    9390400.53   
10             Benicia city, CA        Solano  117605456.02  113264826.18   
11            Berkeley city, CA       Alameda  426069848.79  433634021.57   
12           Brentwood city, CA  Contra Costa  234550508.21  243340685.04   
13            Brisbane city, CA     San Mateo   18239122.54   17771619.19   
14          Burlingame city, CA     San Mateo  127751793.01  135867520.48   
15           Calistoga city, CA          Napa   23320337.16   23375980.56   
16            Campbell city, CA   Santa Clara  197160033.19  194569648.97   
17            Capitola city, CA    Santa Cruz   48901213.28   50805498.21   
18   Carmel-by-the-Sea city, CA      Monterey   34521352.20   34900751.62   
19               Ceres city, CA    Stanislaus  119094076.51  124625298.56   
20      Citrus Heights city, CA    Sacramento  366634028.97  377529031.58   
21             Clayton city, CA  Contra Costa   55904004.52   53979229.03   
22          Cloverdale city, CA        Sonoma   41158765.83   41106644.15   
23              Clovis city, CA        Fresno  455069511.10  439886335.12   
24              Clovis city, CA        Fresno  455069511.10  439886335.12   
25            Coalinga city, CA        Fresno   59272604.68   57166676.21   
26            Coalinga city, CA        Fresno   59272604.68   57166676.21   
27              Colfax city, CA        Placer    9109021.05    8995976.08   
28               Colma town, CA     San Mateo    5612143.78    5616996.75   
29             Concord city, CA  Contra Costa  559808822.15  547371076.92   
..                          ...           ...           ...           ...   
191       Unincorporated_Fresno        Fresno  780513324.85  774699404.13   
192        Unincorporated_Marin         Marin  277664312.89  277592785.05   
193    Unincorporated_Mendocino     Mendocino  282216179.33  278886442.01   
194       Unincorporated_Merced        Merced  414235011.36  412657629.12   
195       Unincorporated_Merced        Merced  414235011.36  412657629.12   
196     Unincorporated_Monterey      Monterey  544923456.42  547461520.11   
197         Unincorporated_Napa          Napa  155415813.03  155052840.57   
198       Unincorporated_Placer        Placer  562283474.59  555937715.30   
199   Unincorporated_Sacramento    Sacramento 2423182694.72 2423963045.88   
200  Unincorporated_San Joaquin   San Joaquin  639393785.34  645455015.91   
201    Unincorporated_San Mateo     San Mateo  240790266.87  245447229.86   
202  Unincorporated_Santa Clara   Santa Clara  397618496.42  396650725.31   
203   Unincorporated_Santa Cruz    Santa Cruz  644101475.50  667970439.44   
204       Unincorporated_Solano        Solano   87885672.22   92308825.74   
205       Unincorporated_Sonoma        Sonoma  764017035.92  757896242.00   
206   Unincorporated_Stanislaus    Stanislaus  416647222.13  420046986.94   
207         Unincorporated_Yolo          Yolo  109860970.63  108694789.95   
208         Union City city, CA       Alameda  260208424.87  269029169.49   
209          Vacaville city, CA        Solano  381443416.75  406247346.50   
210            Vallejo city, CA        Solano  492079646.79  474116196.31   
211       Walnut Creek

In [235]:
#export it
bas_ghg.to_csv("bas_ghg.csv")

In [236]:
#filter vmt df for sums variables
needs_ghg = needs_df[["Place","County_x","15_total_VMT","16_total_VMT","17_total_VMT","18_total_VMT","15_vmt_ghg","16_vmt_ghg","17_vmt_ghg","18_vmt_ghg"]].copy()
needs_ghg

Place      County_x  15_total_VMT  16_total_VMT  \
0              Alameda city, CA       Alameda  339201356.14  332515725.58   
1               Albany city, CA       Alameda   75358653.86   79289953.56   
2      American Canyon city, CA          Napa   72703751.21   73292808.18   
3              Antioch city, CA  Contra Costa  479981026.17  494220993.04   
4             Atherton town, CA     San Mateo   29188637.83   29212188.73   
5              Atwater city, CA        Merced  121240425.59  101584731.21   
6               Auburn city, CA        Placer   68107584.74   60112943.70   
7              Belmont city, CA     San Mateo  129392828.95  128633044.16   
8            Belvedere city, CA         Marin   10223953.28    9833242.91   
9              Benicia city, CA        Solano  131011832.23  117294448.86   
10            Berkeley city, CA       Alameda  436250078.64  458943556.14   
11           Brentwood city, CA  Contra Costa  282720153.65  251922638.03   
12            Brisbane city, CA     San Mateo   20450371.35   18815678.66   
13          Burlingame city, CA     San Mateo  141129558.92  139227691.88   
14           Calistoga city, CA          Napa   24779729.19   24869296.72   
15            Campbell city, CA   Santa Clara  206766272.31  213536814.25   
16            Capitola city, CA    Santa Cruz   26101128.54   24989474.37   
17   Carmel-by-the-Sea city, CA      Monterey   38131050.21   34900751.62   
18               Ceres city, CA    Stanislaus  129784647.59  124625298.56   
19      Citrus Heights city, CA    Sacramento  401516211.14  377435372.44   
20             Clayton city, CA  Contra Costa   61301478.26   58069309.38   
21          Cloverdale city, CA        Sonoma   44527333.44   43278162.38   
22              Clovis city, CA        Fresno  490707002.33  439886335.12   
23            Coalinga city, CA        Fresno   60632548.15   57166676.21   
24              Colfax city, CA        Placer   10191902.49    8995976.08   
25               Colma town, CA     San Mateo    5587221.80    5978840.50   
26             Concord city, CA  Contra Costa  600240471.86  585220750.13   
27        Corte Madera town, CA         Marin   41041020.96   39502579.89   
28              Cotati city, CA        Sonoma   42335628.72   35074628.98   
29           Cupertino city, CA   Santa Clara  266347228.90  269998353.87   
..                          ...           ...           ...           ...   
168    Unincorporated_El Dorado     El Dorado  590493456.54  585251096.58   
169       Unincorporated_Fresno        Fresno  804927450.45  774699404.13   
170        Unincorporated_Marin         Marin  296439002.02  293292297.42   
171    Unincorporated_Mendocino     Mendocino  185036280.14  198041799.59   
172       Unincorporated_Merced        Merced  455378311.62  412657629.12   
173     Unincorporated_Monterey      Monterey  593805556.42  547461520.11   
174         Unincorporated_Napa          Napa  165641309.02  166207310.99   
175       Unincorporated_Placer        Placer  606642896.92  541611908.48   
176   Unincorporated_Sacramento    Sacramento 2402951225.83 2237476223.30   
177  Unincorporated_San Joaquin   San Joaquin  554609911.17  505945169.15   
178    Unincorporated_San Mateo     San Mateo  256210758.06  253861912.76   
179  Unincorporated_Santa Clara   Santa Clara  406730825.88  413609456.21   
180   Unincorporated_Santa Cruz    Santa Cruz  556945370.61  508494073.64   
181       Unincorporated_Solano        Solano  103037902.84   96375119.12   
182       Unincorporated_Sonoma        Sonoma  832241457.97  798969921.95   
183   Unincorporated_Stanislaus    Stanislaus  444431744.99  420046986.94   
184         Unincorporated_Yolo          Yolo   59672280.94   64580712.76   
185         Union City city, CA       Alameda  318452130.84  291992090.80   
186          Vacaville city, CA        Solano  459819785.35  435523997.05   
187            Vallejo city, CA        Solano  545015059.11  491664289.49   
188       Walnut Creek

In [237]:
needs_gas_ghg = needs_gas_usage[["Place","2015_gas_usage","2016_gas_usage","2017_gas_usage","2018_gas_usage","2015_gas_ghg","2016_gas_ghg","2017_gas_ghg","2018_gas_ghg"]].copy()
needs_gas_ghg

Place  2015_gas_usage  2016_gas_usage  2017_gas_usage  \
5            Atwater city, CA       127125.24       106612.43       110424.56   
22            Clovis city, CA       480800.70       432953.34       425902.22   
23          Coalinga city, CA        51814.54        49294.04        52265.22   
35         Dos Palos city, CA        19510.56        19152.54        20085.23   
44         Firebaugh city, CA        25180.90        23955.98        25399.92   
48            Fowler city, CA        21791.16        20731.14        21980.70   
50            Fresno city, CA      2055126.78      1976319.16      1987763.39   
55           Gustine city, CA        24101.28        23659.02        24811.16   
63             Huron city, CA        18885.67        17966.99        19049.94   
65            Kerman city, CA        46487.81        44226.43        46892.16   
67         Kingsburg city, CA        43417.92        42964.74        41525.48   
73        Livingston city, CA        38256.00        37554.00        39382.80   
78         Los Banos city, CA       131218.08       128810.22       135083.00   
83           Mendota city, CA        30507.62        29023.60        30772.98   
85            Merced city, CA       357663.24       299951.03       310676.36   
102      Orange Cove city, CA        23856.00        23607.00        22816.20   
107          Parlier city, CA        37215.36        36826.92        35593.27   
120          Reedley city, CA        72999.36        72237.42        69817.57   
135      San Joaquin city, CA        11137.70        10595.92        11234.58   
144           Sanger city, CA        75862.08        75070.26        72555.52   
153            Selma city, CA        81353.66        77396.26        82061.28   
169     Unincorporated_Fresno       708996.07       682619.84       686714.50   
172     Unincorporated_Merced       342324.36       311268.83       324546.90   
0            Alameda city, CA       422125.19       413828.52       416551.74   
1             Albany city, CA        90928.42        94657.27        92277.76   
2    American Canyon city, CA        69599.39        70128.34        69237.49   
3            Antioch city, CA       445029.94       456014.68       435696.38   
4           Atherton town, CA        30647.03        30760.12        31030.38   
7            Belmont city, CA       138376.26       137708.23       144475.70   
8          Belvedere city, CA        13020.80        12617.83        12331.98   
..                        ...             ...             ...             ...   
187          Vallejo city, CA       560420.06       510039.91       520879.57   
188     Walnut Creek city, CA       419621.82       416490.37       402582.66   
190      Watsonville city, CA       165808.66       156227.04       157002.05   
192          Willits city, CA        13610.80        13725.33        13073.88   
193          Windsor town, CA       107333.09       104291.04       107482.52   
196         Woodside town, CA        26305.52        26361.53        26591.04   
197       Yountville city, CA        13908.47        13613.98        13188.11   
5            Atwater city, CA       127125.24       106612.43       110424.56   
22            Clovis city, CA       480800.70       432953.34       425902.22   
23          Coalinga city, CA        51814.54        49294.04        52265.22   
35         Dos Palos city, CA        19510.56        19152.54        20085.23   
44         Firebaugh city, CA        25180.90        23955.98        25399.92   
48            Fowler city, CA        21791.16        20731.14        21980.70   
50            Fresno city, CA      2055126.78      1976319.16      1987763.39   
55           Gustine city, CA        24101.28        23659.02        24811.16   
63             Huron city, CA        18885.67        17966.99        19049.94   
65            Kerman city, CA        46487.81        44226.43        46892.16   
67         Kingsburg city, CA        43417.92        42

In [238]:
needs_electric_ghg = needs_electric[["Place","15_electric_usage","16_electric_usage","17_electric_usage","18_electric_usage","15_electric_ghg","16_electric_ghg","17_electric_ghg","18_electric_ghg"]].copy()
needs_electric_ghg

Place  15_electric_usage  16_electric_usage  \
0              Alameda city, CA        14791266.59        14500551.34   
1               Albany city, CA         3186131.70         3316790.81   
2      American Canyon city, CA         3723712.26         3752012.08   
3              Antioch city, CA        26474460.03        27127933.06   
4             Atherton town, CA         1073871.86         1077834.46   
5              Atwater city, CA         7562574.59         6342284.50   
6               Auburn city, CA         4173835.67         3688936.44   
7              Belmont city, CA         4848704.15         4825296.45   
8            Belvedere city, CA          456248.97          442128.83   
9              Benicia city, CA         8477598.88         7717220.25   
10            Berkeley city, CA        19930531.67        20745282.31   
11           Brentwood city, CA        14815494.50        13435379.63   
12            Brisbane city, CA          874043.37          809534.17   
13          Burlingame city, CA         5576071.06         5473681.66   
14           Calistoga city, CA         1430246.80         1433554.51   
15            Campbell city, CA         9331658.49         9572244.25   
16            Capitola city, CA         1243226.85         1140792.95   
17   Carmel-by-the-Sea city, CA         1332920.76         1234682.33   
18               Ceres city, CA         9875573.35         9778027.30   
19      Citrus Heights city, CA        25956993.17        23989607.52   
20             Clayton city, CA         3239050.20         3104035.26   
21          Cloverdale city, CA         2050621.43         1994225.95   
22              Clovis city, CA        30741795.76        27682495.37   
23            Coalinga city, CA         3312956.66         3151799.56   
24              Colfax city, CA          636013.05          562123.65   
25               Colma town, CA          235525.99          249976.20   
26             Concord city, CA        35885993.62        35234994.15   
27        Corte Madera town, CA         1767905.64         1713393.77   
28              Cotati city, CA         2368529.74         1990661.43   
29           Cupertino city, CA        11475920.23        11633134.08   
..                          ...                ...                ...   
168    Unincorporated_El Dorado        18752289.92        18691692.93   
169       Unincorporated_Fresno        45332322.60        43645859.55   
170        Unincorporated_Marin        12615332.62        12495207.80   
171    Unincorporated_Mendocino        11227610.27        11322080.70   
172       Unincorporated_Merced        20364590.91        18517123.19   
173     Unincorporated_Monterey        23648230.77        21980153.98   
174         Unincorporated_Napa         7698432.53         7721661.64   
175       Unincorporated_Placer        21972825.06        19629510.61   
176   Unincorporated_Sacramento       147792034.87       138468050.69   
177  Unincorporated_San Joaquin        28515969.98        25763629.49   
178    Unincorporated_San Mateo         9435751.17         9343322.93   
179  Unincorporated_Santa Clara        16080731.82        16396921.09   
180   Unincorporated_Santa Cruz        18596438.67        17040332.54   
181       Unincorporated_Solano         5910211.83         5550696.19   
182       Unincorporated_Sonoma        42242565.83        40597527.00   
183   Unincorporated_Stanislaus        26787507.73        25509029.39   
184         Unincorporated_Yolo         3375478.01         3580243.07   
185         Union City city, CA        10778053.25         9912377.02   
186          Vacaville city, CA        26641706.93        25333348.83   
187            Vallejo city, CA        19637119.04        17871798.52   
188       Walnut Creek city, CA        24962952.39        24776665.15   
189          Waterford city, CA         1973748.47         1813267.64   
190        Watsonville city, CA         5809935.31         5474195.48   
191    West

In [239]:
needs_ghg = needs_ghg.merge(needs_gas_ghg,how="left",on="Place")
needs_ghg = needs_ghg.merge(needs_electric_ghg,how="left",on="Place")
needs_ghg

Place      County_x  15_total_VMT  16_total_VMT  \
0              Alameda city, CA       Alameda  339201356.14  332515725.58   
1               Albany city, CA       Alameda   75358653.86   79289953.56   
2      American Canyon city, CA          Napa   72703751.21   73292808.18   
3              Antioch city, CA  Contra Costa  479981026.17  494220993.04   
4             Atherton town, CA     San Mateo   29188637.83   29212188.73   
5              Atwater city, CA        Merced  121240425.59  101584731.21   
6              Atwater city, CA        Merced  121240425.59  101584731.21   
7               Auburn city, CA        Placer   68107584.74   60112943.70   
8              Belmont city, CA     San Mateo  129392828.95  128633044.16   
9            Belvedere city, CA         Marin   10223953.28    9833242.91   
10             Benicia city, CA        Solano  131011832.23  117294448.86   
11            Berkeley city, CA       Alameda  436250078.64  458943556.14   
12           Brentwood city, CA  Contra Costa  282720153.65  251922638.03   
13            Brisbane city, CA     San Mateo   20450371.35   18815678.66   
14          Burlingame city, CA     San Mateo  141129558.92  139227691.88   
15           Calistoga city, CA          Napa   24779729.19   24869296.72   
16            Campbell city, CA   Santa Clara  206766272.31  213536814.25   
17            Capitola city, CA    Santa Cruz   26101128.54   24989474.37   
18   Carmel-by-the-Sea city, CA      Monterey   38131050.21   34900751.62   
19               Ceres city, CA    Stanislaus  129784647.59  124625298.56   
20      Citrus Heights city, CA    Sacramento  401516211.14  377435372.44   
21             Clayton city, CA  Contra Costa   61301478.26   58069309.38   
22          Cloverdale city, CA        Sonoma   44527333.44   43278162.38   
23              Clovis city, CA        Fresno  490707002.33  439886335.12   
24              Clovis city, CA        Fresno  490707002.33  439886335.12   
25            Coalinga city, CA        Fresno   60632548.15   57166676.21   
26            Coalinga city, CA        Fresno   60632548.15   57166676.21   
27              Colfax city, CA        Placer   10191902.49    8995976.08   
28               Colma town, CA     San Mateo    5587221.80    5978840.50   
29             Concord city, CA  Contra Costa  600240471.86  585220750.13   
..                          ...           ...           ...           ...   
191       Unincorporated_Fresno        Fresno  804927450.45  774699404.13   
192        Unincorporated_Marin         Marin  296439002.02  293292297.42   
193    Unincorporated_Mendocino     Mendocino  185036280.14  198041799.59   
194       Unincorporated_Merced        Merced  455378311.62  412657629.12   
195       Unincorporated_Merced        Merced  455378311.62  412657629.12   
196     Unincorporated_Monterey      Monterey  593805556.42  547461520.11   
197         Unincorporated_Napa          Napa  165641309.02  166207310.99   
198       Unincorporated_Placer        Placer  606642896.92  541611908.48   
199   Unincorporated_Sacramento    Sacramento 2402951225.83 2237476223.30   
200  Unincorporated_San Joaquin   San Joaquin  554609911.17  505945169.15   
201    Unincorporated_San Mateo     San Mateo  256210758.06  253861912.76   
202  Unincorporated_Santa Clara   Santa Clara  406730825.88  413609456.21   
203   Unincorporated_Santa Cruz    Santa Cruz  556945370.61  508494073.64   
204       Unincorporated_Solano        Solano  103037902.84   96375119.12   
205       Unincorporated_Sonoma        Sonoma  832241457.97  798969921.95   
206   Unincorporated_Stanislaus    Stanislaus  444431744.99  420046986.94   
207         Unincorporated_Yolo          Yolo   59672280.94   64580712.76   
208         Union City city, CA       Alameda  318452130.84  291992090.80   
209          Vacaville city, CA        Solano  459819785.35  435523997.05   
210            Vallejo city, CA        Solano  545015059.11  491664289.49   
211       Walnut Creek

In [240]:
#export it
needs_ghg.to_csv("needs_ghg.csv")